### Country Vx Throughput Analysis
 
**Note:**

* Inputs:
  - covax_supply_chain_analytics.analysis_vx_throughput_data
  - covax_supply_chain_analytics.covax_sca_country_dimension
  - covax_supply_chain_analytics.country_dimension.iso_mapping
  - covax_supply_chain_analytics.vx_received_supply
  - covax_supply_chain_analytics.analysis_vx_throughput_supply
  - covax_supply_chain_analytics.owid_covid_data
  - covax_supply_chain_analytics.population_coverage_measures
  - covax_supply_chain_analytics.country_characteristics
* Output:
  - covax_supply_chain_analytics.analysis_vx_throughput_output_daily

* Libraries: 
  - Python

* Built by: Jeremy Cooper
* Current owner: Jeremy Cooper
* Initial Build Date: 04/28/2021
* Latest Build Date: 01/03/2022

### Environment Management

In [0]:
# dbutils.widgets.removeAll()

In [0]:
# # Dataset Name, will be used for the Metastore Table, Folder Name for transformed outputs
# dbutils.widgets.text("Dataset", "dataset_name")

# # Project Name will be used for folder Name for transformed outputs
# dbutils.widgets.text("Project", "project_name")

# # Team name should be consistent with the Blob Storage Container
# dbutils.widgets.text("Partner","partner_name")

# # Team name should be consistent with the Blob Storage Container
# dbutils.widgets.text("Source","data_source")

# dbutils.widgets.text("iso_code", "")

#### Notebook Setup

##### Import any libraries or nested notebooks

In [0]:
import pandas as pd

from delta.tables import *
from pyspark.sql.types import *
from pyspark.sql.functions import *
from pyspark.sql.window import Window

##### Initialize File Paths

In [0]:
storage_root = "/mnt/"+dbutils.widgets.get("Partner")+"/"
storage_branch = "/"+dbutils.widgets.get("Source")+"/" +dbutils.widgets.get("Dataset")

raw_storage_path = storage_root + "raw" +storage_branch
dbfs_raw_storage_path = "/dbfs"+raw_storage_path

transformed_storage_path = storage_root + "transformed" +storage_branch
dbfs_transformed_storage_path = "/dbfs"+transformed_storage_path

print(raw_storage_path)
print(transformed_storage_path)

/mnt/covax-supply-chain-analytics/raw/who/analysis_vx_throughput_output_daily
/mnt/covax-supply-chain-analytics/transformed/who/analysis_vx_throughput_output_daily

##### Define any functions

In [0]:
# function takes the following parameters and will peform a pandas ffill() on a Spark DataFrame

def fill_forward(df, id_column, key_column, fill_column, new_column):

    # Fill null's with last *non null* value in the window
    ff = df.withColumn(
        new_column,
        last(fill_column, True) # True: fill with last non-null
        .over(
            Window.partitionBy(id_column)
            .orderBy(key_column)
            .rowsBetween(-sys.maxsize, 0))
        )
    
    return(ff)
  

### Get Data

In [0]:
iso_code = dbutils.widgets.get("iso_code")

In [0]:
# use this to get iso_code from country
iso_mapping = spark.sql("SELECT * FROM country_dimension.iso_mapping")

# get country level information
country_dimension = spark.sql("SELECT * FROM covax_supply_chain_analytics.covax_sca_country_dimension")

# get supply data
# received_supply = spark.sql("SELECT * FROM covax_supply_chain_analytics.vx_received_supply")
received_supply = spark.sql("SELECT * FROM covax_supply_chain_analytics.linksbridge_delivered_supply")

# get uti_supply
uti_supply = spark.sql("SELECT * FROM covax_supply_chain_analytics.analysis_vx_throughput_supply")

# get dose administration data for comparison
owid = spark.sql("SELECT * FROM covax_supply_chain_analytics.owid_covid_data")

# get population numbers
pop = spark.sql("SELECT * FROM covax_supply_chain_analytics.population_coverage_measures").select('iso_code', 'population_total_both')

# get primary data
who = spark.sql("SELECT * FROM covax_supply_chain_analytics.analysis_vx_throughput_data_cleaned")

# get country characteristics
cc = spark.sql("SELECT * FROM covax_supply_chain_analytics.country_characteristics")

### Transformation

In [0]:
country = country_dimension \
  .select('iso_code', 'country_name_friendly', 'sub_region_name', 'region_name', 'wb_income_group', 'is_amc92', 'affiliation', 'min_vx_rollout_date', 'first_covax_arrival_date', 'first_vx_shipment_received_date') \
#   .filter(col('is_amc92')==1)

display(country)

iso_code country_name_friendly sub_region_name region_name wb_income_group is_amc92 affiliation min_vx_rollout_date first_covax_arrival_date first_vx_shipment_received_date TCA Turks & Caicos Islands Latin America and the Caribbean Americas H 0 null 2021-01-11 null null UKR Ukraine Eastern Europe Europe LM 1 null 2021-02-24 null 2021-02-23 00:00:00 ARE United Arab Emirates Western Asia Asia H 0 null 2020-12-14 null null TON Tonga Polynesia Oceania UM 1 null 2021-04-14 null 2021-03-31 00:00:00 TJK Tajikistan Central Asia Asia LM 1 null 2021-04-07 null 2021-03-08 00:00:00 UGA Uganda Sub-Saharan Africa Africa L 1 African Union 2021-03-10 null 2021-03-05 00:00:00 TKL Tokelau Polynesia Oceania UNK 0 null 2021-07-20 null null TKM Turkmenistan Central Asia Asia UM 0 null 2021-02-24 null null THA Thailand South-eastern Asia Asia UM 0 null 2021-02-28 null null TUV Tuvalu Polynesia Oceania UM 1 null 2021-04-12 null 2021-04-08 00:00:00 TLS Timor-Leste South-eastern Asia Asia LM 1 null 2021-04-07 null 2021-04-05 00:00:00 TGO Togo Sub-Saharan Africa Africa L 1 African Union 2021-03-10 null 2021-03-07 00:00:00 TUR Turkey Western Asia Asia UM 0 null 2021-01-14 null null TUN Tunisia Northern Africa Africa LM 1 African Union 2021-03-13 null 2021-03-09 00:00:00 TTO Trinidad & Tobago Latin America and the Caribbean Americas H 0 null 2021-02-17 null null MKD North Macedonia Southern Europe Europe UM 0 null 2021-02-17 null null COD Democratic Republic of the Congo Sub-Saharan Africa Africa L 1 African Union 2021-03-17 null 2021-03-02 00:00:00 ETH Ethiopia Sub-Saharan Africa Africa L 1 African Union 2021-03-13 null 2021-03-07 00:00:00 GNQ Equatorial Guinea Sub-Saharan Africa Africa UM 0 African Union 2021-02-12 null null FRO Faroe Islands Northern Europe Europe H 0 null 2021-01-29 null null ERI Eritrea Sub-Saharan Africa Africa L 1 African Union null null null FLK Falkland Islands Latin America and the Caribbean Americas UNK 0 null 2021-02-15 null null DMA Dominica Latin America and the Caribbean Americas UM 1 null 2021-02-12 null 2021-02-09 00:00:00 DJI Djibouti Sub-Saharan Africa Africa LM 1 African Union 2021-03-15 null 2021-03-06 00:00:00 DOM Dominican Republic Latin America and the Caribbean Americas UM 0 null 2021-02-16 null null PRK North Korea Eastern Asia Asia L 1 null null null null DNK Denmark Northern Europe Europe H 0 European Union 2020-12-08 null null SWZ Eswatini Sub-Saharan Africa Africa LM 1 African Union 2021-03-18 null 2021-03-13 00:00:00 EST Estonia Northern Europe Europe H 0 European Union 2020-12-23 null null SLV El Salvador Latin America and the Caribbean Americas LM 1 null 2021-02-17 null 2021-02-17 00:00:00 ECU Ecuador Latin America and the Caribbean Americas UM 0 null 2021-01-20 null null EGY Egypt Northern Africa Africa LM 1 African Union 2021-01-24 null 2020-12-10 00:00:00 ZMB Zambia Sub-Saharan Africa Africa LM 1 African Union 2021-04-14 null 2021-04-12 00:00:00 URY Uruguay Latin America and the Caribbean Americas H 0 null 2021-02-27 null null VIR U.S. Virgin Islands Latin America and the Caribbean Americas H 0 null 2020-12-14 null null WLF Wallis & Futuna Polynesia Oceania UNK 0 null 2021-03-19 null null GBR UK Northern Europe Europe H 0 null 2020-12-21 null null VUT Vanuatu Melanesia Oceania LM 1 null 2021-06-02 null 2021-05-19 00:00:00 YEM Yemen Western Asia Asia L 1 null 2021-04-20 null 2021-03-31 00:00:00 VEN Venezuela Latin America and the Caribbean Americas UNK 0 null 2021-02-22 null null USA US Northern America Americas H 0 null 2020-12-13 null null VNM Vietnam South-eastern Asia Asia LM 1 null 2021-03-08 null 2021-02-24 00:00:00 ALA Åland Islands Northern Europe Europe UNK 0 null null null null UMI U.S. Outlying Islands Micronesia Oceania UNK 0 null null null null ZWE Zimbabwe Sub-Saharan Africa Africa LM 1 African Union 2021-02-18 null 2021-02-15 00:00:00 ESH Western Sahara Northern Africa Africa UNK 0 African Union null null null UZB Uzbekistan Central Asia Asia LM 1 null 2021-04-01 null 2021-03-17 00:00:00 

In [0]:
owid1 = owid \
  .select('iso_code', 'date', 'total_vaccinations_int') \
  .toDF('iso_code', 'date', 'total_doses_owid')

display(owid1)

iso_code date total_doses_owid ARM 2020-02-03 null ARM 2020-02-04 null ARM 2020-02-05 null ARM 2020-02-06 null ARM 2020-02-07 null ARM 2020-02-08 null ARM 2020-02-09 null ARM 2020-02-10 null ARM 2020-02-11 null ARM 2020-02-12 null ARM 2020-02-13 null ARM 2020-02-14 null ARM 2020-02-15 null ARM 2020-02-16 null ARM 2020-02-17 null ARM 2020-02-18 null ARM 2020-02-19 null ARM 2020-02-20 null ARM 2020-02-21 null ARM 2020-02-22 null ARM 2020-02-23 null ARM 2020-02-24 null ARM 2020-02-25 null ARM 2020-02-26 null ARM 2020-02-27 null ARM 2020-02-28 null ARM 2020-02-29 null ARM 2020-03-01 null ARM 2020-03-02 null ARM 2020-03-03 null ARM 2020-03-04 null ARM 2020-03-05 null ARM 2020-03-06 null ARM 2020-03-07 null ARM 2020-03-08 null ARM 2020-03-09 null ARM 2020-03-10 null ARM 2020-03-11 null ARM 2020-03-12 null ARM 2020-03-13 null ARM 2020-03-14 null ARM 2020-03-15 null ARM 2020-03-16 null ARM 2020-03-17 null ARM 2020-03-18 null ARM 2020-03-19 null ARM 2020-03-20 null ARM 2020-03-21 null ARM 2020-03-22 null ARM 2020-03-23 null ARM 2020-03-24 null ARM 2020-03-25 null ARM 2020-03-26 null ARM 2020-03-27 null ARM 2020-03-28 null ARM 2020-03-29 null ARM 2020-03-30 null ARM 2020-03-31 null ARM 2020-04-01 null ARM 2020-04-02 null ARM 2020-04-03 null ARM 2020-04-04 null ARM 2020-04-05 null ARM 2020-04-06 null ARM 2020-04-07 null ARM 2020-04-08 null ARM 2020-04-09 null ARM 2020-04-10 null ARM 2020-04-11 null ARM 2020-04-12 null ARM 2020-04-13 null ARM 2020-04-14 null ARM 2020-04-15 null ARM 2020-04-16 null ARM 2020-04-17 null ARM 2020-04-18 null ARM 2020-04-19 null ARM 2020-04-20 null ARM 2020-04-21 null ARM 2020-04-22 null ARM 2020-04-23 null ARM 2020-04-24 null ARM 2020-04-25 null ARM 2020-04-26 null ARM 2020-04-27 null ARM 2020-04-28 null ARM 2020-04-29 null ARM 2020-04-30 null ARM 2020-05-01 null ARM 2020-05-02 null ARM 2020-05-03 null ARM 2020-05-04 null ARM 2020-05-05 null ARM 2020-05-06 null ARM 2020-05-07 null ARM 2020-05-08 null ARM 2020-05-09 null ARM 2020-05-10 null ARM 2020-05-11 null ARM 2020-05-12 null ARM 2020-05-13 null ARM 2020-05-14 null ARM 2020-05-15 null ARM 2020-05-16 null ARM 2020-05-17 null ARM 2020-05-18 null ARM 2020-05-19 null ARM 2020-05-20 null ARM 2020-05-21 null ARM 2020-05-22 null ARM 2020-05-23 null ARM 2020-05-24 null ARM 2020-05-25 null ARM 2020-05-26 null ARM 2020-05-27 null ARM 2020-05-28 null ARM 2020-05-29 null ARM 2020-05-30 null ARM 2020-05-31 null ARM 2020-06-01 null ARM 2020-06-02 null ARM 2020-06-03 null ARM 2020-06-04 null ARM 2020-06-05 null ARM 2020-06-06 null ARM 2020-06-07 null ARM 2020-06-08 null ARM 2020-06-09 null ARM 2020-06-10 null ARM 2020-06-11 null ARM 2020-06-12 null ARM 2020-06-13 null ARM 2020-06-14 null ARM 2020-06-15 null ARM 2020-06-16 null ARM 2020-06-17 null ARM 2020-06-18 null ARM 2020-06-19 null ARM 2020-06-20 null ARM 2020-06-21 null ARM 2020-06-22 null ARM 2020-06-23 null ARM 2020-06-24 null ARM 2020-06-25 null ARM 2020-06-26 null ARM 2020-06-27 null ARM 2020-06-28 null ARM 2020-06-29 null ARM 2020-06-30 null ARM 2020-07-01 null ARM 2020-07-02 null ARM 2020-07-03 null ARM 2020-07-04 null ARM 2020-07-05 null ARM 2020-07-06 null ARM 2020-07-07 null ARM 2020-07-08 null ARM 2020-07-09 null ARM 2020-07-10 null ARM 2020-07-11 null ARM 2020-07-12 null ARM 2020-07-13 null ARM 2020-07-14 null ARM 2020-07-15 null ARM 2020-07-16 null ARM 2020-07-17 null ARM 2020-07-18 null ARM 2020-07-19 null ARM 2020-07-20 null ARM 2020-07-21 null ARM 2020-07-22 null ARM 2020-07-23 null ARM 2020-07-24 null ARM 2020-07-25 null ARM 2020-07-26 null ARM 2020-07-27 null ARM 2020-07-28 null ARM 2020-07-29 null ARM 2020-07-30 null ARM 2020-07-31 null ARM 2020-08-01 null ARM 2020-08-02 null ARM 2020-08-03 null ARM 2020-08-04 null ARM 2020-08-05 null ARM 2020-08-06 null ARM 2020-08-07 null ARM 2020-08-08 null ARM 2020-08-09 null ARM 2020-08-10 null ARM 2020-08-11 null ARM 2020-08-12 null ARM 2020-08-13 null ARM 2020-08-14 null ARM 2020-08-15 null ARM 2020-08-16 null ARM 2020-08-17 null ARM 2020-08-18 null ARM 2020-

In [0]:
# supply side
# aggregate to received date
# generate cumulative supply
received_supply1 = received_supply \
  .filter(col('iso_code').isNotNull()) \
  .withColumn('received_date', to_date(col('date'))) \
  .groupBy('iso_code', 'received_date').agg(sum('doses_delivered').alias('doses_received')) \
  .withColumn('cumulative_doses_received', sum('doses_received').over(Window.partitionBy('iso_code').orderBy('received_date').rowsBetween(-sys.maxsize, 0))) \
  .withColumn('max_cumulative_doses_received', max('cumulative_doses_received').over(Window.partitionBy('iso_code', 'received_date'))) \
  .filter((col('max_cumulative_doses_received')==col('cumulative_doses_received')) | col('max_cumulative_doses_received').isNull()) \
  .drop('max_cumulative_doses_received') \
  .filter(col('doses_received')!=0) \
  .toDF('iso_code', 'date', 'doses_received', 'cumulative_doses_received')

display(received_supply1.orderBy('iso_code', 'received_date'))
display(received_supply1.filter(col('iso_code')==iso_code))

iso_code date doses_received cumulative_doses_received ABW 2021-03-01 28343.0 28343.0 ABW 2021-04-01 56209.0 84552.0 ABW 2021-05-01 41018.0 125570.0 ABW 2021-06-01 14412.0 139982.0 ABW 2021-07-01 12378.0 152360.0 ABW 2021-08-01 12285.0 164645.0 ABW 2021-09-01 7152.0 171797.0 ABW 2021-10-01 3550.0 175347.0 ABW 2021-11-01 2461.0 177808.0 ABW 2021-12-01 2328.0 180136.0 ABW 2022-01-01 2949.0 183085.0 ABW 2022-02-01 1518.0 184603.0 ABW 2022-03-01 1673.0 186276.0 ABW 2022-04-01 1080.0 187356.0 ABW 2022-05-01 108.0 187464.0 AFG 2021-02-01 500000.0 500000.0 AFG 2021-03-01 468000.0 968000.0 AFG 2021-06-01 700000.0 1668000.0 AFG 2021-07-01 3436850.0 5104850.0 AFG 2021-08-01 144000.0 5248850.0 AFG 2021-11-01 151200.0 5400050.0 AFG 2021-12-01 4504000.0 9904050.0 AFG 2022-01-01 840000.0 1.074405E7 AFG 2022-02-01 388800.0 1.113285E7 AFG 2022-03-01 1836000.0 1.296885E7 AGO 2021-03-01 824000.0 824000.0 AGO 2021-04-01 495000.0 1319000.0 AGO 2021-05-01 40000.0 1359000.0 AGO 2021-06-01 125620.0 1484620.0 AGO 2021-07-01 50000.0 1534620.0 AGO 2021-08-01 1797110.0 3331730.0 AGO 2021-09-01 2166690.0 5498420.0 AGO 2021-10-01 5072610.0 1.057103E7 AGO 2021-11-01 4757960.0 1.532899E7 AGO 2021-12-01 1.154879E7 2.687778E7 AGO 2022-02-01 666900.0 2.754468E7 AIA 2021-02-01 4322.0 4322.0 AIA 2021-03-01 1561.0 5883.0 AIA 2021-04-01 1705.0 7588.0 AIA 2021-05-01 8300.0 15888.0 AIA 2021-06-01 1481.0 17369.0 AIA 2021-07-01 2644.0 20013.0 AIA 2021-08-01 292.0 20305.0 AIA 2021-09-01 139.0 20444.0 AIA 2021-10-01 133.0 20577.0 AIA 2021-11-01 1128.0 21705.0 AIA 2021-12-01 609.0 22314.0 AIA 2022-01-01 1282.0 23596.0 AIA 2022-02-01 788.0 24384.0 AIA 2022-03-01 604.0 24988.0 AIA 2022-04-01 453.0 25441.0 ALB 2021-01-01 975.0 975.0 ALB 2021-02-01 207210.0 208185.0 ALB 2021-03-01 72970.0 281155.0 ALB 2021-04-01 454220.0 735375.0 ALB 2021-05-01 132010.0 867385.0 ALB 2021-06-01 197453.0 1064838.0 ALB 2021-07-01 258360.0 1323198.0 ALB 2021-08-01 325302.0 1648500.0 ALB 2021-09-01 267011.0 1915511.0 ALB 2021-10-01 305400.0 2220911.0 ALB 2021-11-01 94880.0 2315791.0 ALB 2021-12-01 375000.0 2690791.0 ALB 2022-01-01 85262.0 2776053.0 ALB 2022-02-01 196851.0 2972904.0 ALB 2022-03-01 70677.0 3043581.0 ALB 2022-04-01 52510.0 3096091.0 AND 2021-01-01 634.0 634.0 AND 2021-02-01 2145.0 2779.0 AND 2021-03-01 7438.0 10217.0 AND 2021-04-01 26400.0 36617.0 AND 2021-05-01 2891.0 39508.0 AND 2021-06-01 35654.0 75162.0 AND 2021-07-01 15422.0 90584.0 AND 2021-08-01 14926.0 105510.0 AND 2021-09-01 6725.0 112235.0 AND 2021-10-01 2752.0 114987.0 AND 2021-12-01 13983.0 128970.0 AND 2022-01-01 25242.0 154212.0 AND 2022-02-01 12200.0 166412.0 AND 2022-03-01 993.0 167405.0 AND 2022-04-01 304.0 167709.0 ARE 2020-12-01 3000000.0 3000000.0 ARE 2021-01-01 667578.0 3667578.0 ARE 2021-02-01 2954929.0 6622507.0 ARE 2021-03-01 2516809.0 9139316.0 ARE 2021-04-01 2463027.0 1.1602343E7 ARE 2021-05-01 2555266.0 1.4157609E7 ARE 2021-06-01 2740968.0 1.6898577E7 ARE 2021-07-01 1576713.0 1.847529E7 ARE 2021-08-01 1499601.0 1.9974891E7 ARE 2021-09-01 2082749.0 2.205764E7 ARE 2021-10-01 1179662.0 2.3237302E7 ARE 2021-11-01 793216.0 2.4030518E7 ARE 2021-12-01 616726.0 2.4647244E7 ARE 2022-01-01 1205509.0 2.5852753E7 ARE 2022-02-01 678216.0 2.6530969E7 ARE 2022-03-01 402722.0 2.6933691E7 ARE 2022-04-01 202567.0 2.7136258E7 ARE 2022-05-01 35536.0 2.7171794E7 ARG 2020-12-01 300150.0 300150.0 ARG 2021-01-01 520000.0 820150.0 ARG 2021-02-01 3430175.0 4250325.0 ARG 2021-03-01 4389920.0 8640245.0 ARG 2021-04-01 6225135.0 1.486538E7 ARG 2021-05-01 7199445.0 2.2064825E7 ARG 2021-06-01 9009050.0 3.1073875E7 ARG 2021-07-01 1.6132395E7 4.720627E7 ARG 2021-08-01 1.15276E7 5.873387E7 ARG 2021-09-01 1.6422675E7 7.5156545E7 ARG 2021-10-01 1.526317E7 9.0419715E7 ARG 2021-11-01 9121141.0 9.9540856E7 ARG 2021-12-01 4319580.0 1.03860436E8 ARG 2022-01-01 3623490.0 1.07483926E8 ARG 2022-02-01 4666040.0 1.12149966E8 ARG 2022-03-01 2260980.0 1.14410946E8 ARG 2022-04-01 3140570.0 1.17551516E8 ARM 2021-03-01 24000.0 24000.0 ARM 2021-04-01 15000.0

iso_code date doses_received cumulative_doses_received UGA 2021-03-01 964000.0 964000.0 UGA 2021-06-01 175200.0 1139200.0 UGA 2021-07-01 586080.0 1725280.0 UGA 2021-08-01 428080.0 2153360.0 UGA 2021-09-01 3312050.0 5465410.0 UGA 2021-10-01 3447400.0 8912810.0 UGA 2021-11-01 8178280.0 1.709109E7 UGA 2021-12-01 1.683465E7 3.392574E7 UGA 2022-01-01 1684800.0 3.561054E7 UGA 2022-02-01 2431660.0 3.80422E7 UGA 2022-03-01 5550330.0 4.359253E7

In [0]:
# alternate supply, sourced by Marta
uti_supply1 = fill_forward(uti_supply, 'iso_code', 'date', 'cumulative_doses_received_uti', 'cumulative_doses_received_uti')

uti_supply1 = uti_supply1 \
  .withColumn('cumulative_doses_received_uti', col('cumulative_doses_received_uti').cast(DoubleType())) \
  .withColumn('date', to_date(col('date'))) \
  .fillna(0) \
  .withColumn('doses_received', lag(col('cumulative_doses_received_uti')).over(Window.partitionBy('iso_code').orderBy('date'))) \
  .withColumn('doses_received', col('cumulative_doses_received_uti') - col('doses_received')) \
  .withColumn('doses_received', when(col('doses_received').isNull(), col('cumulative_doses_received_uti')).otherwise(col('doses_received'))) \
  .select('iso_code', 'date', 'doses_received', 'cumulative_doses_received_uti') \
  .toDF('iso_code', 'date', 'doses_received', 'cumulative_doses_received') \

display(uti_supply1)

iso_code date doses_received cumulative_doses_received AFG 2021-03-01 968000.0 968000.0 AFG 2021-07-01 3.4088E7 3.5056E7 AFG 2021-08-01 800.0 3.50568E7 AFG 2021-09-01 0.0 3.50568E7 AFG 2021-10-01 -2.9808E7 5248800.0 AFG 2021-11-01 151200.0 5400000.0 AFG 2021-12-01 3004000.0 8404000.0 AGO 2021-05-01 1509620.0 1509620.0 AGO 2021-06-01 101310.0 1610930.0 AGO 2021-07-01 224765.0 1835695.0 AGO 2021-08-01 1762125.0 3597820.0 AGO 2021-09-01 0.0 3597820.0 AGO 2021-10-01 2349690.0 5947510.0 AGO 2021-11-01 1.4031252E7 1.9978762E7 AGO 2021-12-01 1.280383E7 3.2782592E7 AGO 2022-01-01 4039575.0 3.6822167E7 AIA 2021-06-01 41000.0 41000.0 AIA 2021-07-01 0.0 41000.0 AIA 2021-08-01 0.0 41000.0 AIA 2021-09-01 0.0 41000.0 AIA 2021-10-01 0.0 41000.0 AIA 2021-11-01 7020.0 48020.0 AIA 2021-12-01 0.0 48020.0 AIA 2022-01-01 0.0 48020.0 AIA 2022-02-01 6240.0 54260.0 AND 2021-03-01 0.0 0.0 AND 2021-04-01 0.0 0.0 AND 2021-05-01 92100.0 92100.0 AND 2021-06-01 56760.0 148860.0 AND 2021-07-01 54000.0 202860.0 AND 2021-08-01 0.0 202860.0 AND 2021-09-01 0.0 202860.0 AND 2021-10-01 4680.0 207540.0 AND 2021-11-01 42120.0 249660.0 AND 2021-12-01 20000.0 269660.0 AND 2022-02-01 0.0 269660.0 ARE 2021-09-01 0.0 0.0 ARG 2021-03-01 0.0 0.0 ARG 2021-04-01 0.0 0.0 ARG 2021-05-01 0.0 0.0 ARG 2021-06-01 0.0 0.0 ARG 2021-07-01 7.666778E7 7.666778E7 ARG 2021-08-01 2.777905E7 1.0444683E8 ARG 2021-10-01 7.093914E7 1.7538597E8 ARG 2021-11-01 2.259489E7 1.9798086E8 ARG 2021-12-01 7043880.0 2.0502474E8 ARG 2022-01-01 9425520.0 2.1445026E8 ATG 2021-05-01 10000.0 10000.0 ATG 2021-07-01 0.0 10000.0 ATG 2021-08-01 130000.0 140000.0 ATG 2021-09-01 0.0 140000.0 ATG 2021-12-01 0.0 140000.0 AUS 2021-04-01 0.0 0.0 AUS 2021-05-01 0.0 0.0 AUS 2021-06-01 0.0 0.0 AUS 2021-07-01 6.151244E7 6.151244E7 AUS 2021-08-01 0.0 6.151244E7 AUS 2021-09-01 0.0 6.151244E7 AUS 2021-11-01 0.0 6.151244E7 AUS 2021-12-01 0.0 6.151244E7 AUS 2022-01-01 0.0 6.151244E7 AUS 2022-02-01 0.0 6.151244E7 AUT 2021-02-01 0.0 0.0 AUT 2021-03-01 0.0 0.0 AUT 2021-04-01 0.0 0.0 AUT 2021-05-01 0.0 0.0 AUT 2021-06-01 1.8138186E7 1.8138186E7 AUT 2021-07-01 0.0 1.8138186E7 AUT 2021-08-01 3638220.0 2.1776406E7 AUT 2021-09-01 9865300.0 3.1641706E7 AUT 2021-10-01 7637014.0 3.927872E7 AUT 2021-11-01 2004346.0 4.1283066E7 AZE 2021-03-01 0.0 0.0 AZE 2021-04-01 0.0 0.0 AZE 2021-05-01 1632040.0 1632040.0 AZE 2021-06-01 7387684.0 9019724.0 AZE 2021-07-01 3614938.0 1.2634662E7 AZE 2021-08-01 0.0 1.2634662E7 AZE 2021-09-01 0.0 1.2634662E7 AZE 2021-10-01 0.0 1.2634662E7 AZE 2021-11-01 0.0 1.2634662E7 AZE 2021-12-01 0.0 1.2634662E7 AZE 2022-01-01 2.2044552E7 3.4679214E7 AZE 2022-02-01 1077966.0 3.575718E7 BDI 2021-10-01 500000.0 500000.0 BDI 2021-11-01 151200.0 651200.0 BDI 2021-12-01 0.0 651200.0 BDI 2022-01-01 151200.0 802400.0 BEL 2021-02-01 0.0 0.0 BEL 2021-03-01 0.0 0.0 BEL 2021-04-01 0.0 0.0 BEL 2021-05-01 1.52E7 1.52E7 BEL 2021-06-01 9200000.0 2.44E7 BEL 2021-07-01 4400000.0 2.88E7 BEL 2021-08-01 0.0 2.88E7 BEL 2021-09-01 0.0 2.88E7 BEL 2021-10-01 0.0 2.88E7 BEL 2021-11-01 0.0 2.88E7 BEL 2021-12-01 0.0 2.88E7 BEL 2022-01-01 0.0 2.88E7 BEL 2022-02-01 0.0 2.88E7 BEN 2021-05-01 347000.0 347000.0 BEN 2021-06-01 0.0 347000.0 BEN 2021-07-01 302400.0 649400.0 BEN 2021-08-01 0.0 649400.0 BEN 2021-09-01 385080.0 1034480.0 BEN 2021-10-01 55200.0 1089680.0 BEN 2021-11-01 0.0 1089680.0 BEN 2021-12-01 1315200.0 2404880.0 BEN 2022-01-01 0.0 2404880.0 BFA 2021-05-01 115000.0 115000.0 BFA 2021-06-01 200.0 115200.0 BFA 2021-07-01 302400.0 417600.0 BFA 2021-08-01 57860.0 475460.0 BFA 2021-09-01 400000.0 875460.0 BFA 2021-10-01 875200.0 1750660.0 BFA 2021-11-01 168400.0 1919060.0 BFA 2021-12-01 2551590.0 4470650.0 BFA 2022-01-01 0.0 4470650.0 BGD 2022-02-01 2.9649502E8 2.9649502E8 BLR 2021-03-01 0.0 0.0 BLR 2021-04-01 0.0 0.0 BLR 2021-05-01 2551280.0 2551280.0 BLR 2021-06-01 1640500.0 4191780.0 BLR 2021-07-01 1315870.0 5507650.0 BLR 2021-08-01 1893850.0 7401500.0 BLR 2021-09-01 2904390.0 1.030589E7 BLR 2021-10-01 1310288.0 1.1616178E7 BLR 2021-11-01 46

In [0]:
# define supply threshold
supply_threshold = 0.0

In [0]:
df_flags = who.select('iso_code', 'date', 'is_latest_week_reported', 'manual_adjustment', 'is_data_error', 'to_remove')

display(df_flags)

iso_code date is_latest_week_reported manual_adjustment is_data_error to_remove SOM 2021-09-01 1 0 0 0 FRA 2021-07-18 0 1 0 0 ABW 2021-09-17 0 0 0 0 ABW 2021-10-29 0 0 0 0 FRA 2021-04-25 0 1 0 0 SOM 2021-06-02 1 0 0 0 SOM 2021-05-30 1 0 0 0 ABW 2021-02-26 0 0 0 0 ABW 2022-02-18 0 0 0 0 FRA 2022-02-27 0 1 0 0 SOM 2021-04-20 1 0 0 0 ABW 2021-07-23 0 0 0 0 SOM 2021-07-06 1 0 0 0 ABW 2022-04-29 0 0 0 0 FRA 2021-08-22 0 1 0 0 ABW 2022-03-18 0 0 0 0 ABW 2021-06-18 0 0 0 0 SOM 2021-09-06 1 0 0 0 ABW 2022-04-08 0 0 0 0 SOM 2021-06-22 1 0 0 0 SOM 2021-04-14 1 0 0 0 SOM 2021-09-28 1 0 0 0 SOM 2021-10-26 1 0 0 0 ABW 2021-08-09 0 0 0 0 ABW 2022-02-04 0 0 0 0 FRA 2021-10-24 0 1 0 0 ABW 2021-03-19 0 0 0 0 ABW 2021-08-06 0 0 0 0 ABW 2021-09-03 0 0 0 0 FRA 2021-08-15 0 1 0 0 SOM 2021-10-12 1 0 0 0 ABW 2021-07-30 0 0 0 0 FRA 2021-05-30 0 1 0 0 FRA 2021-02-23 0 1 0 0 SOM 2021-10-17 1 0 0 0 FRA 2021-08-29 0 1 0 0 SOM 2021-12-26 1 0 0 0 FRA 2021-03-09 0 1 0 0 FRA 2021-05-09 0 1 0 0 ABW 2021-12-31 0 0 0 0 ABW 2022-03-11 0 0 0 0 SOM 2021-04-05 1 0 0 0 ABW 2021-06-11 0 0 0 0 SOM 2021-06-18 1 0 0 0 ABW 2021-05-21 0 0 0 0 ABW 2021-03-05 0 0 0 0 FRA 2022-04-03 0 1 0 0 ABW 2021-06-04 0 0 0 0 SOM 2022-02-06 1 0 0 0 FRA 2021-12-19 0 1 0 0 ABW 2021-10-08 0 0 0 0 ABW 2021-10-15 0 0 0 0 SOM 2021-06-12 1 0 0 0 SOM 2021-09-26 1 0 0 0 SOM 2021-04-19 1 0 0 0 ABW 2021-11-12 0 0 0 0 SOM 2021-09-23 1 0 0 0 ABW 2021-08-13 0 0 0 0 SOM 2021-09-22 1 0 0 0 FRA 2021-04-04 0 1 0 0 FRA 2022-04-24 0 1 0 0 SOM 2021-10-06 1 0 0 0 ABW 2022-02-11 0 0 0 0 FRA 2021-11-28 0 1 0 0 FRA 2021-05-16 0 1 0 0 SOM 2021-04-15 1 0 0 0 SOM 2021-04-18 1 0 0 0 FRA 2021-12-26 0 1 0 0 ABW 2021-08-27 0 0 0 0 ABW 2021-02-19 0 0 0 0 ABW 2021-04-30 0 0 0 0 FRA 2022-02-13 0 1 0 0 SOM 2022-04-26 1 0 0 0 SOM 2021-06-29 1 0 0 0 SOM 2021-06-06 1 0 0 0 FRA 2022-03-20 0 1 0 0 SOM 2021-08-26 1 0 0 0 SOM 2021-09-15 1 0 0 0 ABW 2021-04-16 0 0 0 0 FRA 2021-04-18 0 1 0 0 SOM 2021-05-27 1 0 0 0 ABW 2022-04-01 0 0 0 0 SOM 2022-04-05 1 0 0 0 SOM 2021-09-11 1 0 0 0 ABW 2021-09-10 0 0 0 0 FRA 2022-01-02 0 1 0 0 ABW 2022-03-04 0 0 0 0 ABW 2021-10-01 0 0 0 0 SOM 2021-05-31 1 0 0 0 FRA 2021-10-17 0 1 1 0 SOM 2021-04-08 1 0 0 0 SOM 2021-05-01 1 0 0 0 SOM 2021-06-09 1 0 0 0 ABW 2021-12-23 0 0 0 0 FRA 2022-02-20 0 1 0 0 ABW 2021-10-22 0 0 0 0 ABW 2021-05-07 0 0 0 0 ABW 2021-03-12 0 0 0 0 FRA 2022-03-13 0 1 0 0 SOM 2021-03-23 1 0 0 0 SOM 2022-04-11 1 0 0 0 FRA 2021-03-23 0 1 0 0 SOM 2021-06-20 1 0 0 0 FRA 2021-12-12 0 1 0 0 FRA 2021-07-04 0 1 0 0 SOM 2021-09-29 1 0 0 0 FRA 2021-03-16 0 1 0 0 SOM 2021-06-14 1 0 0 0 SOM 2021-04-28 1 0 0 0 FRA 2022-01-30 0 1 0 0 SOM 2021-12-23 1 0 0 0 SOM 2021-04-25 1 0 0 0 SOM 2021-05-02 1 0 0 0 SOM 2022-05-08 1 0 0 0 ABW 2021-07-09 0 0 0 0 FRA 2021-07-11 0 1 0 0 SOM 2021-12-20 1 0 0 0 ABW 2022-03-25 0 0 0 0 FRA 2021-09-05 0 1 0 0 FRA 2021-05-02 0 1 0 0 FRA 2022-03-06 0 1 0 0 SOM 2022-03-17 1 0 0 0 SOM 2021-08-02 1 0 0 0 SOM 2021-06-08 1 0 0 0 SOM 2021-06-01 1 0 0 0 SOM 2021-11-21 1 0 0 0 ABW 2021-04-09 0 0 0 0 ABW 2022-01-28 0 0 0 0 FRA 2021-08-01 0 1 0 0 FRA 2021-02-16 0 1 0 0 SOM 2021-12-09 1 0 0 0 SOM 2021-08-30 1 0 0 0 ABW 2022-02-25 0 0 0 0 ABW 2022-04-22 0 0 0 0 SOM 2022-02-10 1 0 0 0 SOM 2021-08-21 1 0 0 0 ABW 2021-12-17 0 0 0 0 FRA 2021-06-06 0 1 0 0 ABW 2021-05-28 0 0 0 0 SOM 2021-05-24 1 0 0 0 ABW 2022-04-15 0 0 0 0 ABW 2021-09-24 0 0 0 0 FRA 2021-03-02 0 1 0 0 FRA 2021-12-05 0 1 0 0 FRA 2021-11-21 0 1 0 0 ABW 2021-06-25 0 0 0 0 SOM 2022-03-09 1 0 0 0 SOM 2021-05-16 1 0 0 0 FRA 2021-05-23 0 1 0 0 SOM 2021-07-11 1 0 0 0 FRA 2021-06-20 0 1 0 0 ABW 2021-08-20 0 0 0 0 FRA 2021-10-31 0 1 0 0 SOM 2021-06-28 1 0 0 0 SOM 2021-11-13 1 0 0 0 SOM 2021-07-08 1 0 0 0 FRA 2022-04-10 0 1 0 0 ABW 2022-01-07 0 0 0 0 SOM 2021-06-23 1 0 0 0 SOM 2021-06-17 1 0 0 0 ABW 2021-05-14 0 0 0 0 SOM 2022-04-04 1 0 0 0 ABW 2021-03-26 0 0 0 0 SOM 2021-10-31 1 0 0 0 ABW 2021-07-16 0 0 0 0 ABW 2021-12-03 0 0 0 0 SOM 2021-10-14 1 0 0 0 SOM 2022-02-28 1 0 0 0 ABW 2022-01-14 0 0 0 0 FRA 2021-08-08 0 1 0 0 ABW 2021-0

In [0]:
# filter out records we want to drop
# generate prev total_doses value
# generate days since prev reported date, if it's the first value > 0, then calc use days since vx intro to smooth things out
# generate daily_rate_per_week, our key measurement
w = Window.partitionBy('iso_code').orderBy('date')
df1 = who \
  .filter(col('to_remove')==0) \
  .filter(col('to_remove_1st')==0) \
  .filter(col('to_remove_2nd')==0) \

df1 = df1 \
  .join(country, 'iso_code', how='left') \
  .filter(col('country_name_friendly').isNotNull()) \
  .withColumn('min_date', min('date').over(Window.partitionBy('iso_code'))) \
  .withColumn('min_vx_rollout_date', when(col('min_vx_rollout_date')>=col('min_date'), col('min_date')-1).otherwise(col('min_vx_rollout_date'))) \
  .withColumn('days_since_vx_intro', datediff(col('date'), col('min_vx_rollout_date'))) \
  .withColumn('date_prev', lag(col('date')).over(w)) \
  .withColumn('days_since_vx_intro', datediff(col('date'), col('min_vx_rollout_date'))) \
  .withColumn('days_since_prev', when(col('date_prev').isNull(), col('days_since_vx_intro')).otherwise(datediff(col('date'), col('date_prev'))))

# create date range from vx rollout date to max report date
df_daterange = df1 \
  .withColumn('date_max', max('date').over(Window.partitionBy('iso_code'))) \
  .withColumn('min_vx_rollout_date', to_date(col('min_vx_rollout_date'))) \
  .select('iso_code', 'min_vx_rollout_date', 'date_max') \
  .drop_duplicates() \
  .withColumn('date', explode(expr('sequence(min_vx_rollout_date, date_max, interval 1 day)'))) \
  .select('iso_code', 'date') \

# subset to input measures
df2 = df1 \
  .select('iso_code', 'date', 'min_vx_rollout_date', 'total_doses', 'at_least_one_dose', 'fully_vaccinated', 'persons_booster_add_dose') \

# join and set vx rollout date to 0 as starting point (if currently null)
df_inter = df_daterange \
  .join(df2, ['iso_code', 'date'], how='left') \
  .withColumn('date_start', min('date').over(Window.partitionBy('iso_code'))) \
  .withColumn('total_doses', when((col('date')==col('date_start')) & (col('total_doses').isNull()), 0).otherwise(col('total_doses'))) \
  .withColumn('at_least_one_dose', when((col('date')==col('date_start')) & (col('at_least_one_dose').isNull()), 0).otherwise(col('at_least_one_dose'))) \
  .withColumn('fully_vaccinated', when((col('date')==col('date_start')) & (col('fully_vaccinated').isNull()), 0).otherwise(col('fully_vaccinated'))) \
  .withColumn('persons_booster_add_dose', when((col('date')==col('date_start')) & (col('persons_booster_add_dose').isNull()), 0).otherwise(col('persons_booster_add_dose'))) \

# create placeholder columns of correct data type
df_inter = df_inter \
  .withColumn('total_doses_int', col('total_doses').cast(IntegerType())) \
  .withColumn('at_least_one_dose_int', col('at_least_one_dose').cast(IntegerType())) \
  .withColumn('fully_vaccinated_int', col('fully_vaccinated').cast(IntegerType())) \
  .withColumn('persons_booster_add_dose_int', col('persons_booster_add_dose').cast(IntegerType())) \

# pandas_udf requires a schema to be defined
schema = df_inter.schema

# interpolation function
@pandas_udf(schema, functionType=PandasUDFType.GROUPED_MAP)
def interpolate_measures(df):
    df.sort_values(by=['iso_code', 'date'], ascending=True, inplace=True)
    df['total_doses_int'] = df['total_doses_int'].interpolate(method='linear', limit_direction='forward')
    df['at_least_one_dose_int'] = df['at_least_one_dose_int'].interpolate(method='linear', limit_direction='forward')
    df['fully_vaccinated_int'] = df['fully_vaccinated_int'].interpolate(method='linear', limit_direction='forward')
    df['persons_booster_add_dose_int'] = df['persons_booster_add_dose_int'].interpolate(method='linear', limit_direction='forward')
    return df

df_inter = df_inter.groupBy('iso_code').apply(interpolate_measures)

df3 = df_inter \
  .join(country.select('iso_code', 'country_name_friendly'), 'iso_code', how='left') \
  .withColumn('is_original_reported', when(col('min_vx_rollout_date').isNotNull(), 1).otherwise(0)) \
  .drop('total_doses', 'at_least_one_dose', 'fully_vaccinated', 'persons_booster_add_dose', 'date_start') \
  .select('iso_code', 'date', 'country_name_friendly', 'min_vx_rollout_date', 'total_doses_int', 'at_least_one_dose_int', 'fully_vaccinated_int', 'persons_booster_add_dose_int', 'is_original_reported') \
  .toDF('iso_code', 'date', 'country_name_friendly', 'min_vx_rollout_date', 'total_doses', 'at_least_one_dose', 'fully_vaccinated', 'persons_booster_add_dose', 'is_original_reported') \
  .withColumn('min_vx_rollout_date', min('min_vx_rollout_date').over(Window.partitionBy('iso_code')))

# join demand and supply, full join, fill forward, and then filter to "left join"
# take out 10% for wastage assumption

# df4 = df3 \
#   .join(uti_supply1, ['iso_code', 'date'], how='full')
# df4 = fill_forward(df4, 'iso_code', 'date', 'cumulative_doses_received', 'cumulative_doses_received')
# df4 = df4.filter(col('country_name_friendly').isNotNull()) \

df4 = df3 \
  .join(received_supply1, ['iso_code', 'date'], how='full')
df4 = fill_forward(df4, 'iso_code', 'date', 'cumulative_doses_received', 'cumulative_doses_received')
df4 = df4.withColumn('cumulative_doses_received', col('cumulative_doses_received')*.9)
df4 = df4.filter(col('country_name_friendly').isNotNull()) \

# join supply with demand
df4 = df4 \
  .withColumn('cumulative_doses_received', when(col('cumulative_doses_received') < col('total_doses'), col('total_doses')).otherwise(col('cumulative_doses_received'))) \
  .withColumn('total_doses_prev_week', lag(col('total_doses')).over(w)) \
  .withColumn('effective_supply', col('cumulative_doses_received') - col('total_doses_prev_week')) \
  .withColumn('cumulative_supply_20', col('cumulative_doses_received')*supply_threshold) \
  .withColumn('supply_constrained', when(col('effective_supply') < col('cumulative_supply_20'), 1) \
              .when(col('effective_supply') >= col('cumulative_supply_20'), 0)) \
  .drop('total_doses_prev_week')

display(df4)

/databricks/spark/python/pyspark/sql/pandas/group_ops.py:81: UserWarning: It is preferred to use 'applyInPandas' over this API. This API will be deprecated in the future releases. See SPARK-28264 for more details.
 warnings.warn(

iso_code date country_name_friendly min_vx_rollout_date total_doses at_least_one_dose fully_vaccinated persons_booster_add_dose is_original_reported doses_received cumulative_doses_received effective_supply cumulative_supply_20 supply_constrained ABW 2021-02-17 Aruba 2021-02-17 0 0 0 0 0 null null null null null ABW 2021-02-18 Aruba 2021-02-17 6 6 0 0 0 null null null null null ABW 2021-02-19 Aruba 2021-02-17 12 12 0 0 1 null null null null null ABW 2021-02-20 Aruba 2021-02-17 424 424 0 0 0 null null null null null ABW 2021-02-21 Aruba 2021-02-17 836 836 0 0 0 null null null null null ABW 2021-02-22 Aruba 2021-02-17 1248 1248 0 0 0 null null null null null ABW 2021-02-23 Aruba 2021-02-17 1660 1660 0 0 0 null null null null null ABW 2021-02-24 Aruba 2021-02-17 2072 2072 0 0 0 null null null null null ABW 2021-02-25 Aruba 2021-02-17 2484 2484 0 0 0 null null null null null ABW 2021-02-26 Aruba 2021-02-17 2896 2896 0 0 1 null null null null null ABW 2021-02-27 Aruba 2021-02-17 3751 3751 0 0 0 null null null null null ABW 2021-02-28 Aruba 2021-02-17 4606 4606 0 0 0 null null null null null ABW 2021-03-01 Aruba 2021-02-17 5461 5461 0 0 0 28343.0 25508.7 20902.7 0.0 0 ABW 2021-03-02 Aruba 2021-02-17 6316 6316 0 0 0 null 25508.7 20047.7 0.0 0 ABW 2021-03-03 Aruba 2021-02-17 7171 7171 0 0 0 null 25508.7 19192.7 0.0 0 ABW 2021-03-04 Aruba 2021-02-17 8026 8026 0 0 0 null 25508.7 18337.7 0.0 0 ABW 2021-03-05 Aruba 2021-02-17 8882 8882 0 0 1 null 25508.7 17482.7 0.0 0 ABW 2021-03-06 Aruba 2021-02-17 9138 9138 0 0 0 null 25508.7 16626.7 0.0 0 ABW 2021-03-07 Aruba 2021-02-17 9395 9395 0 0 0 null 25508.7 16370.7 0.0 0 ABW 2021-03-08 Aruba 2021-02-17 9652 9652 0 0 0 null 25508.7 16113.7 0.0 0 ABW 2021-03-09 Aruba 2021-02-17 9908 9908 0 0 0 null 25508.7 15856.7 0.0 0 ABW 2021-03-10 Aruba 2021-02-17 10165 10165 0 0 0 null 25508.7 15600.7 0.0 0 ABW 2021-03-11 Aruba 2021-02-17 10422 10422 0 0 0 null 25508.7 15343.7 0.0 0 ABW 2021-03-12 Aruba 2021-02-17 10679 10679 0 0 1 null 25508.7 15086.7 0.0 0 ABW 2021-03-13 Aruba 2021-02-17 11243 10835 408 0 0 null 25508.7 14829.7 0.0 0 ABW 2021-03-14 Aruba 2021-02-17 11807 10991 816 0 0 null 25508.7 14265.7 0.0 0 ABW 2021-03-15 Aruba 2021-02-17 12371 11147 1224 0 0 null 25508.7 13701.7 0.0 0 ABW 2021-03-16 Aruba 2021-02-17 12935 11303 1632 0 0 null 25508.7 13137.7 0.0 0 ABW 2021-03-17 Aruba 2021-02-17 13499 11459 2040 0 0 null 25508.7 12573.7 0.0 0 ABW 2021-03-18 Aruba 2021-02-17 14063 11615 2448 0 0 null 25508.7 12009.7 0.0 0 ABW 2021-03-19 Aruba 2021-02-17 14628 11772 2856 0 1 null 25508.7 11445.7 0.0 0 ABW 2021-03-20 Aruba 2021-02-17 15624 11923 3700 0 0 null 25508.7 10880.7 0.0 0 ABW 2021-03-21 Aruba 2021-02-17 16620 12075 4544 0 0 null 25508.7 9884.7 0.0 0 ABW 2021-03-22 Aruba 2021-02-17 17616 12227 5389 0 0 null 25508.7 8888.7 0.0 0 ABW 2021-03-23 Aruba 2021-02-17 18613 12379 6233 0 0 null 25508.7 7892.700000000001 0.0 0 ABW 2021-03-24 Aruba 2021-02-17 19609 12531 7078 0 0 null 25508.7 6895.700000000001 0.0 0 ABW 2021-03-25 Aruba 2021-02-17 20605 12683 7922 0 0 null 25508.7 5899.700000000001 0.0 0 ABW 2021-03-26 Aruba 2021-02-17 21602 12835 8767 0 1 null 25508.7 4903.700000000001 0.0 0 ABW 2021-03-27 Aruba 2021-02-17 22652 13621 9030 0 0 null 25508.7 3906.7000000000007 0.0 0 ABW 2021-03-28 Aruba 2021-02-17 23702 14408 9294 0 0 null 25508.7 2856.7000000000007 0.0 0 ABW 2021-03-29 Aruba 2021-02-17 24753 15194 9558 0 0 null 25508.7 1806.7000000000007 0.0 0 ABW 2021-03-30 Aruba 2021-02-17 25803 15981 9822 0 0 null 25803.0 1050.0 0.0 0 ABW 2021-03-31 Aruba 2021-02-17 26853 16767 10086 0 0 null 26853.0 1050.0 0.0 0 ABW 2021-04-01 Aruba 2021-02-17 27904 17554 10350 0 1 56209.0 76096.8 49243.8 0.0 0 ABW 2021-04-02 Aruba 2021-02-17 28844 18372 10472 0 0 null 76096.8 48192.8 0.0 0 ABW 2021-04-03 Aruba 2021-02-17 29785 19191 10594 0 0 null 76096.8 47252.8 0.0 0 ABW 2021-04-04 Aruba 2021-02-17 30726 20009 10716 0 0 null 76096.8 46311.8 0.0 0 ABW 2021-04-05 Aruba 2021-02-17 31667 20828 10839 0 0 null 76096.8 45370.

In [0]:
# key
# _td = total_doses
# _1d = at_least_one_dose
# _fv = fully_vaccinated

# define n days
days_in_weeks4 = 27
days_in_weeks8 = 55

# window partitions
w_rolling_avg_4 = Window.partitionBy('iso_code').orderBy('date').rowsBetween(-days_in_weeks4, 0)
w_rolling_avg_8 = Window.partitionBy('iso_code').orderBy('date').rowsBetween(-days_in_weeks8, 0)
w_rolling_avg_4_lastweek = Window.partitionBy('iso_code').orderBy('date').rowsBetween(-34, -7)
w_rolling_avg_4_lastmonth = Window.partitionBy('iso_code').orderBy('date').rowsBetween(-55, -28)


# create measure set for total_doses
var1 = 'total_doses'
var2 = 'daily_rate_td'
var3 = 'rolling_4_week_avg_td'
var4 = 'rolling_8_week_avg_td'
var5 = 'rolling_4_week_avg_td_lastweek'
var6 = 'rolling_4_week_avg_td_lastmonth'
var7 = 'max_rolling_4_week_avg_td'
var8 = 'med_rolling_4_week_avg_td'

# calculate
df5 = df4 \
  .withColumn('prev_total', lag(col(var1)).over(Window.partitionBy('iso_code').orderBy('date'))) \
  .withColumn(var2, when((col(var1) - col('prev_total')).isNull(), col(var1)).otherwise((col(var1) - col('prev_total')))) \
  .withColumn(var3, avg(var2).over(w_rolling_avg_4)) \
  .withColumn(var4, avg(var2).over(w_rolling_avg_8)) \
  .withColumn(var5, avg(var2).over(w_rolling_avg_4_lastweek)) \
  .withColumn(var6, avg(var2).over(w_rolling_avg_4_lastmonth)) \
  .withColumn(var7, max(var3).over(Window.partitionBy('iso_code'))) \
  .withColumn(var8, expr('percentile_approx({0}, .5)'.format(var3)).over(Window.partitionBy('iso_code'))) \
  .drop('prev_total')


# create measure set for at_least_one_dose
var1 = 'at_least_one_dose'
var2 = 'daily_rate_1d'
var3 = 'rolling_4_week_avg_1d'
var4 = 'rolling_8_week_avg_1d'
var5 = 'rolling_4_week_avg_1d_lastweek'
var6 = 'rolling_4_week_avg_1d_lastmonth'
var7 = 'max_rolling_4_week_avg_1d'
var8 = 'med_rolling_4_week_avg_1d'

# calculate
df6 = df5 \
  .withColumn('prev_total', lag(col(var1)).over(Window.partitionBy('iso_code').orderBy('date'))) \
  .withColumn(var2, when((col(var1) - col('prev_total')).isNull(), col(var1)).otherwise((col(var1) - col('prev_total')))) \
  .withColumn(var3, avg(var2).over(w_rolling_avg_4)) \
  .withColumn(var4, avg(var2).over(w_rolling_avg_8)) \
  .withColumn(var5, avg(var2).over(w_rolling_avg_4_lastweek)) \
  .withColumn(var6, avg(var2).over(w_rolling_avg_4_lastmonth)) \
  .withColumn(var7, max(var3).over(Window.partitionBy('iso_code'))) \
  .withColumn(var8, expr('percentile_approx({0}, .5)'.format(var3)).over(Window.partitionBy('iso_code'))) \
  .drop('prev_total')


# create measure set for fully_vaccinated
var1 = 'fully_vaccinated'
var2 = 'daily_rate_fv'
var3 = 'rolling_4_week_avg_fv'
var4 = 'rolling_8_week_avg_fv'
var5 = 'rolling_4_week_avg_fv_lastweek'
var6 = 'rolling_4_week_avg_fv_lastmonth'
var7 = 'max_rolling_4_week_avg_fv'
var8 = 'med_rolling_4_week_avg_fv'

# calculate
df7 = df6 \
  .withColumn('prev_total', lag(col(var1)).over(Window.partitionBy('iso_code').orderBy('date'))) \
  .withColumn(var2, when((col(var1) - col('prev_total')).isNull(), col(var1)).otherwise((col(var1) - col('prev_total')))) \
  .withColumn(var3, avg(var2).over(w_rolling_avg_4)) \
  .withColumn(var4, avg(var2).over(w_rolling_avg_8)) \
  .withColumn(var5, avg(var2).over(w_rolling_avg_4_lastweek)) \
  .withColumn(var6, avg(var2).over(w_rolling_avg_4_lastmonth)) \
  .withColumn(var7, max(var3).over(Window.partitionBy('iso_code'))) \
  .withColumn(var8, expr('percentile_approx({0}, .5)'.format(var3)).over(Window.partitionBy('iso_code'))) \
  .drop('prev_total')


df8 = df7

display(df8.orderBy('iso_code', 'date'))

iso_code date country_name_friendly min_vx_rollout_date total_doses at_least_one_dose fully_vaccinated persons_booster_add_dose is_original_reported doses_received cumulative_doses_received effective_supply cumulative_supply_20 supply_constrained daily_rate_td rolling_4_week_avg_td rolling_8_week_avg_td rolling_4_week_avg_td_lastweek rolling_4_week_avg_td_lastmonth max_rolling_4_week_avg_td med_rolling_4_week_avg_td daily_rate_1d rolling_4_week_avg_1d rolling_8_week_avg_1d rolling_4_week_avg_1d_lastweek rolling_4_week_avg_1d_lastmonth max_rolling_4_week_avg_1d med_rolling_4_week_avg_1d daily_rate_fv rolling_4_week_avg_fv rolling_8_week_avg_fv rolling_4_week_avg_fv_lastweek rolling_4_week_avg_fv_lastmonth max_rolling_4_week_avg_fv med_rolling_4_week_avg_fv ABW 2021-02-17 Aruba 2021-02-17 0 0 0 0 0 null null null null null 0 0.0 0.0 null null 1639.392857142857 264.0 0 0.0 0.0 null null 1266.607142857143 89.57142857142857 0 0.0 0.0 null null 1027.3214285714287 81.42857142857143 ABW 2021-02-18 Aruba 2021-02-17 6 6 0 0 0 null null null null null 6 3.0 3.0 null null 1639.392857142857 264.0 6 3.0 3.0 null null 1266.607142857143 89.57142857142857 0 0.0 0.0 null null 1027.3214285714287 81.42857142857143 ABW 2021-02-19 Aruba 2021-02-17 12 12 0 0 1 null null null null null 6 4.0 4.0 null null 1639.392857142857 264.0 6 4.0 4.0 null null 1266.607142857143 89.57142857142857 0 0.0 0.0 null null 1027.3214285714287 81.42857142857143 ABW 2021-02-20 Aruba 2021-02-17 424 424 0 0 0 null null null null null 412 106.0 106.0 null null 1639.392857142857 264.0 412 106.0 106.0 null null 1266.607142857143 89.57142857142857 0 0.0 0.0 null null 1027.3214285714287 81.42857142857143 ABW 2021-02-21 Aruba 2021-02-17 836 836 0 0 0 null null null null null 412 167.2 167.2 null null 1639.392857142857 264.0 412 167.2 167.2 null null 1266.607142857143 89.57142857142857 0 0.0 0.0 null null 1027.3214285714287 81.42857142857143 ABW 2021-02-22 Aruba 2021-02-17 1248 1248 0 0 0 null null null null null 412 208.0 208.0 null null 1639.392857142857 264.0 412 208.0 208.0 null null 1266.607142857143 89.57142857142857 0 0.0 0.0 null null 1027.3214285714287 81.42857142857143 ABW 2021-02-23 Aruba 2021-02-17 1660 1660 0 0 0 null null null null null 412 237.14285714285714 237.14285714285714 null null 1639.392857142857 264.0 412 237.14285714285714 237.14285714285714 null null 1266.607142857143 89.57142857142857 0 0.0 0.0 null null 1027.3214285714287 81.42857142857143 ABW 2021-02-24 Aruba 2021-02-17 2072 2072 0 0 0 null null null null null 412 259.0 259.0 0.0 null 1639.392857142857 264.0 412 259.0 259.0 0.0 null 1266.607142857143 89.57142857142857 0 0.0 0.0 0.0 null 1027.3214285714287 81.42857142857143 ABW 2021-02-25 Aruba 2021-02-17 2484 2484 0 0 0 null null null null null 412 276.0 276.0 3.0 null 1639.392857142857 264.0 412 276.0 276.0 3.0 null 1266.607142857143 89.57142857142857 0 0.0 0.0 0.0 null 1027.3214285714287 81.42857142857143 ABW 2021-02-26 Aruba 2021-02-17 2896 2896 0 0 1 null null null null null 412 289.6 289.6 4.0 null 1639.392857142857 264.0 412 289.6 289.6 4.0 null 1266.607142857143 89.57142857142857 0 0.0 0.0 0.0 null 1027.3214285714287 81.42857142857143 ABW 2021-02-27 Aruba 2021-02-17 3751 3751 0 0 0 null null null null null 855 341.0 341.0 106.0 null 1639.392857142857 264.0 855 341.0 341.0 106.0 null 1266.607142857143 89.57142857142857 0 0.0 0.0 0.0 null 1027.3214285714287 81.42857142857143 ABW 2021-02-28 Aruba 2021-02-17 4606 4606 0 0 0 null null null null null 855 383.8333333333333 383.8333333333333 167.2 null 1639.392857142857 264.0 855 383.8333333333333 383.8333333333333 167.2 null 1266.607142857143 89.57142857142857 0 0.0 0.0 0.0 null 1027.3214285714287 81.42857142857143 ABW 2021-03-01 Aruba 2021-02-17 5461 5461 0 0 0 28343.0 25508.7 20902.7 0.0 0 855 420.0769230769231 420.0769230769231 208.0 null 1639.392857142857 264.0 855 420.0769230769231 420.0769230769231 208.0 null 1266.607142857143 89.57142857142857 0 0.0 0.0 0.0 null 1027.3214285714287 81.428571428571

In [0]:
# plot the interpolated series
print(iso_code)
display(df8.filter(col('iso_code')==iso_code).orderBy('date'))

UGA

iso_code date country_name_friendly min_vx_rollout_date total_doses at_least_one_dose fully_vaccinated persons_booster_add_dose is_original_reported doses_received cumulative_doses_received effective_supply cumulative_supply_20 supply_constrained daily_rate_td rolling_4_week_avg_td rolling_8_week_avg_td rolling_4_week_avg_td_lastweek rolling_4_week_avg_td_lastmonth max_rolling_4_week_avg_td med_rolling_4_week_avg_td daily_rate_1d rolling_4_week_avg_1d rolling_8_week_avg_1d rolling_4_week_avg_1d_lastweek rolling_4_week_avg_1d_lastmonth max_rolling_4_week_avg_1d med_rolling_4_week_avg_1d daily_rate_fv rolling_4_week_avg_fv rolling_8_week_avg_fv rolling_4_week_avg_fv_lastweek rolling_4_week_avg_fv_lastmonth max_rolling_4_week_avg_fv med_rolling_4_week_avg_fv UGA 2021-03-10 Uganda 2021-03-10 0 0 0 0 0 null 867600.0 null 0.0 null 0 0.0 0.0 null null 183164.67857142858 27581.964285714286 0 0.0 0.0 null null 164794.92857142858 18112.178571428572 0 0.0 0.0 null null 311943.3214285714 4508.928571428572 UGA 2021-03-11 Uganda 2021-03-10 405 405 0 0 0 null 867600.0 867600.0 0.0 0 405 202.5 202.5 null null 183164.67857142858 27581.964285714286 405 202.5 202.5 null null 164794.92857142858 18112.178571428572 0 0.0 0.0 null null 311943.3214285714 4508.928571428572 UGA 2021-03-12 Uganda 2021-03-10 810 810 0 0 0 null 867600.0 867195.0 0.0 0 405 270.0 270.0 null null 183164.67857142858 27581.964285714286 405 270.0 270.0 null null 164794.92857142858 18112.178571428572 0 0.0 0.0 null null 311943.3214285714 4508.928571428572 UGA 2021-03-13 Uganda 2021-03-10 1215 1215 0 0 1 null 867600.0 866790.0 0.0 0 405 303.75 303.75 null null 183164.67857142858 27581.964285714286 405 303.75 303.75 null null 164794.92857142858 18112.178571428572 0 0.0 0.0 null null 311943.3214285714 4508.928571428572 UGA 2021-03-14 Uganda 2021-03-10 3719 1104 0 0 0 null 867600.0 866385.0 0.0 0 2504 743.8 743.8 null null 183164.67857142858 27581.964285714286 -111 220.8 220.8 null null 164794.92857142858 18112.178571428572 0 0.0 0.0 null null 311943.3214285714 4508.928571428572 UGA 2021-03-15 Uganda 2021-03-10 6223 994 0 0 0 null 867600.0 863881.0 0.0 0 2504 1037.1666666666667 1037.1666666666667 null null 183164.67857142858 27581.964285714286 -110 165.66666666666666 165.66666666666666 null null 164794.92857142858 18112.178571428572 0 0.0 0.0 null null 311943.3214285714 4508.928571428572 UGA 2021-03-16 Uganda 2021-03-10 8727 883 0 0 0 null 867600.0 861377.0 0.0 0 2504 1246.7142857142858 1246.7142857142858 null null 183164.67857142858 27581.964285714286 -111 126.14285714285714 126.14285714285714 null null 164794.92857142858 18112.178571428572 0 0.0 0.0 null null 311943.3214285714 4508.928571428572 UGA 2021-03-17 Uganda 2021-03-10 11231 773 0 0 0 null 867600.0 858873.0 0.0 0 2504 1403.875 1403.875 0.0 null 183164.67857142858 27581.964285714286 -110 96.625 96.625 0.0 null 164794.92857142858 18112.178571428572 0 0.0 0.0 0.0 null 311943.3214285714 4508.928571428572 UGA 2021-03-18 Uganda 2021-03-10 13735 662 0 0 0 null 867600.0 856369.0 0.0 0 2504 1526.111111111111 1526.111111111111 202.5 null 183164.67857142858 27581.964285714286 -111 73.55555555555556 73.55555555555556 202.5 null 164794.92857142858 18112.178571428572 0 0.0 0.0 0.0 null 311943.3214285714 4508.928571428572 UGA 2021-03-19 Uganda 2021-03-10 16240 552 0 0 0 null 867600.0 853865.0 0.0 0 2505 1624.0 1624.0 270.0 null 183164.67857142858 27581.964285714286 -110 55.2 55.2 270.0 null 164794.92857142858 18112.178571428572 0 0.0 0.0 0.0 null 311943.3214285714 4508.928571428572 UGA 2021-03-20 Uganda 2021-03-10 18744 441 0 0 0 null 867600.0 851360.0 0.0 0 2504 1704.0 1704.0 303.75 null 183164.67857142858 27581.964285714286 -111 40.09090909090909 40.09090909090909 303.75 null 164794.92857142858 18112.178571428572 0 0.0 0.0 0.0 null 311943.3214285714 4508.928571428572 UGA 2021-03-21 Uganda 2021-03-10 21248 331 0 0 0 null 867600.0 848856.0 0.0 0 2504 1770.6666666666667 1770.6666666666667 743.8 null 183164.67857142858 27581.964285714286 -

In [0]:
df9 = df8 \
  .join(cc, 'iso_code', how='inner') \
  .join(owid1, ['iso_code', 'date'],  how='left') \
  .withColumn('rolling_4_week_avg_td_per100', (col('rolling_4_week_avg_td')/col('population'))*100) \
  .withColumn('rolling_8_week_avg_td_per100', (col('rolling_8_week_avg_td')/col('population'))*100) \
  .withColumn('max_rolling_4_week_avg_td_per100', (col('max_rolling_4_week_avg_td')/col('population'))*100) \

df_date_week = df9 \
  .filter(col('is_original_reported')==1) \
  .select('iso_code', 'date', 'total_doses') \
  .withColumn('date_week', to_date(next_day(date_add(col('date'), -1), 'Fri'))) \
  .withColumn('week_max', max(col('total_doses')).over(Window.partitionBy('iso_code', 'date_week'))) \
  .filter(col('week_max')==col('total_doses')) \
  .withColumn('date_max', max(col('date')).over(Window.partitionBy('iso_code', 'date_week'))) \
  .filter(col('date_max')==col('date')) \
  .withColumn('max_date_week', max(col('date_week')).over(Window.partitionBy('iso_code'))) \
  .withColumn('is_latest', when(col('max_date_week')==col('date_week'), 1).otherwise(0)) \
  .withColumn('week_num', row_number().over(Window.partitionBy('iso_code').orderBy('date_week'))) \
  .select('iso_code', 'date', 'date_week', 'max_date_week', 'is_latest', 'week_num')

display(df_date_week.groupBy('iso_code', 'date_week').agg(count('*')).filter(col('count(1)')>1))

df10 = df9 \
  .join(df_date_week, ['iso_code', 'date'], how='left') \
  .join(df_flags.select('iso_code', 'is_latest_week_reported').drop_duplicates(), 'iso_code', how='left') \

df11 = df10 \
  .withColumn('prev_week_val', lag(col('total_doses')).over(Window.partitionBy('iso_code').orderBy('date'))) \
  .withColumn('no_change_from_previous', when(col('total_doses')==col('prev_week_val'), 1).otherwise(0)) \
  .drop('prev_week_val')

display(df11.orderBy('iso_code', 'date'))

iso_code date_week count(1)

iso_code date country_name_friendly min_vx_rollout_date total_doses at_least_one_dose fully_vaccinated persons_booster_add_dose is_original_reported doses_received cumulative_doses_received effective_supply cumulative_supply_20 supply_constrained daily_rate_td rolling_4_week_avg_td rolling_8_week_avg_td rolling_4_week_avg_td_lastweek rolling_4_week_avg_td_lastmonth max_rolling_4_week_avg_td med_rolling_4_week_avg_td daily_rate_1d rolling_4_week_avg_1d rolling_8_week_avg_1d rolling_4_week_avg_1d_lastweek rolling_4_week_avg_1d_lastmonth max_rolling_4_week_avg_1d med_rolling_4_week_avg_1d daily_rate_fv rolling_4_week_avg_fv rolling_8_week_avg_fv rolling_4_week_avg_fv_lastweek rolling_4_week_avg_fv_lastmonth max_rolling_4_week_avg_fv med_rolling_4_week_avg_fv entity_name population who_region unicef_region world_bank_region world_bank_income_group covax_status amc_status covax_participation_modality procurement_mechanism date_accessed total_doses_owid rolling_4_week_avg_td_per100 rolling_8_week_avg_td_per100 max_rolling_4_week_avg_td_per100 date_week max_date_week is_latest week_num is_latest_week_reported no_change_from_previous ABW 2021-02-17 Aruba 2021-02-17 0 0 0 0 0 null null null null null 0 0.0 0.0 null null 1639.392857142857 264.0 0 0.0 0.0 null null 1266.607142857143 89.57142857142857 0 0.0 0.0 null null 1027.3214285714287 81.42857142857143 Aruba 106766 Other Other LAC HIC Non-COVAX Non-COVAX null null 2021-09-14 null 0.0 0.0 1.5355008683877425 null null null null 0 0 ABW 2021-02-18 Aruba 2021-02-17 6 6 0 0 0 null null null null null 6 3.0 3.0 null null 1639.392857142857 264.0 6 3.0 3.0 null null 1266.607142857143 89.57142857142857 0 0.0 0.0 null null 1027.3214285714287 81.42857142857143 Aruba 106766 Other Other LAC HIC Non-COVAX Non-COVAX null null 2021-09-14 null 0.0028098832961804317 0.0028098832961804317 1.5355008683877425 null null null null 0 0 ABW 2021-02-19 Aruba 2021-02-17 12 12 0 0 1 null null null null null 6 4.0 4.0 null null 1639.392857142857 264.0 6 4.0 4.0 null null 1266.607142857143 89.57142857142857 0 0.0 0.0 null null 1027.3214285714287 81.42857142857143 Aruba 106766 Other Other LAC HIC Non-COVAX Non-COVAX null null 2021-09-14 null 0.003746511061573909 0.003746511061573909 1.5355008683877425 2021-02-19 2022-04-29 0 1 0 0 ABW 2021-02-20 Aruba 2021-02-17 424 424 0 0 0 null null null null null 412 106.0 106.0 null null 1639.392857142857 264.0 412 106.0 106.0 null null 1266.607142857143 89.57142857142857 0 0.0 0.0 null null 1027.3214285714287 81.42857142857143 Aruba 106766 Other Other LAC HIC Non-COVAX Non-COVAX null null 2021-09-14 null 0.09928254313170859 0.09928254313170859 1.5355008683877425 null null null null 0 0 ABW 2021-02-21 Aruba 2021-02-17 836 836 0 0 0 null null null null null 412 167.2 167.2 null null 1639.392857142857 264.0 412 167.2 167.2 null null 1266.607142857143 89.57142857142857 0 0.0 0.0 null null 1027.3214285714287 81.42857142857143 Aruba 106766 Other Other LAC HIC Non-COVAX Non-COVAX null null 2021-09-14 null 0.1566041623737894 0.1566041623737894 1.5355008683877425 null null null null 0 0 ABW 2021-02-22 Aruba 2021-02-17 1248 1248 0 0 0 null null null null null 412 208.0 208.0 null null 1639.392857142857 264.0 412 208.0 208.0 null null 1266.607142857143 89.57142857142857 0 0.0 0.0 null null 1027.3214285714287 81.42857142857143 Aruba 106766 Other Other LAC HIC Non-COVAX Non-COVAX null null 2021-09-14 null 0.19481857520184329 0.19481857520184329 1.5355008683877425 null null null null 0 0 ABW 2021-02-23 Aruba 2021-02-17 1660 1660 0 0 0 null null null null null 412 237.14285714285714 237.14285714285714 null null 1639.392857142857 264.0 412 237.14285714285714 237.14285714285714 null null 1266.607142857143 89.57142857142857 0 0.0 0.0 null null 1027.3214285714287 81.42857142857143 Aruba 106766 Other Other LAC HIC Non-COVAX Non-COVAX null null 2021-09-14 null 0.22211458436473894 0.22211458436473894 1.5355008683877425 null null null null 0 0 ABW 2021-02-24 Aruba 2021-02-17 2072 2072 0 0 0 null n

In [0]:
df12 = df11 \
  .select('iso_code', 'entity_name', 'population', 'date', 'is_original_reported', 
          'cumulative_doses_received', 'effective_supply',
          'total_doses_owid', 'total_doses', 'at_least_one_dose', 'fully_vaccinated', 'persons_booster_add_dose',
          'daily_rate_td', 'rolling_4_week_avg_td', 'max_rolling_4_week_avg_td', 'med_rolling_4_week_avg_td', 
          'rolling_4_week_avg_td_lastweek', 'rolling_4_week_avg_td_lastmonth', 'rolling_8_week_avg_td', 
          'rolling_4_week_avg_td_per100', 'rolling_8_week_avg_td_per100', 'max_rolling_4_week_avg_td_per100',
          'daily_rate_1d', 'rolling_4_week_avg_1d', 'daily_rate_fv', 'rolling_4_week_avg_fv', 
          'is_latest', 'is_latest_week_reported', 'no_change_from_previous')

df12 = df12.join(who.select('iso_code', 'date_accessed').drop_duplicates(), 'iso_code', how='left')

display(df12.orderBy('iso_code', 'date').filter(col('iso_code')==iso_code))
display(df12.filter(col('is_latest')==1))
display(df12.filter(col('is_latest_weeK_reported')==1))

iso_code entity_name population date is_original_reported cumulative_doses_received effective_supply total_doses_owid total_doses at_least_one_dose fully_vaccinated persons_booster_add_dose daily_rate_td rolling_4_week_avg_td max_rolling_4_week_avg_td med_rolling_4_week_avg_td rolling_4_week_avg_td_lastweek rolling_4_week_avg_td_lastmonth rolling_8_week_avg_td rolling_4_week_avg_td_per100 rolling_8_week_avg_td_per100 max_rolling_4_week_avg_td_per100 daily_rate_1d rolling_4_week_avg_1d daily_rate_fv rolling_4_week_avg_fv is_latest is_latest_week_reported no_change_from_previous date_accessed UGA Uganda 45741007 2021-03-10 0 867600.0 null 338.3333333333333 0 0 0 0 0 0.0 183164.67857142858 27581.964285714286 null null 0.0 0.0 0.0 0.4004386667119694 0 0.0 0 0.0 null 1 0 2022-05-09 UGA Uganda 45741007 2021-03-11 0 867600.0 867600.0 676.6666666666666 405 405 0 0 405 202.5 183164.67857142858 27581.964285714286 null null 202.5 4.427099735692308E-4 4.427099735692308E-4 0.4004386667119694 405 202.5 0 0.0 null 1 0 2022-05-09 UGA Uganda 45741007 2021-03-12 0 867600.0 867195.0 1015.0 810 810 0 0 405 270.0 183164.67857142858 27581.964285714286 null null 270.0 5.902799647589744E-4 5.902799647589744E-4 0.4004386667119694 405 270.0 0 0.0 null 1 0 2022-05-09 UGA Uganda 45741007 2021-03-13 1 867600.0 866790.0 1215.0 1215 1215 0 0 405 303.75 183164.67857142858 27581.964285714286 null null 303.75 6.640649603538462E-4 6.640649603538462E-4 0.4004386667119694 405 303.75 0 0.0 0 1 0 2022-05-09 UGA Uganda 45741007 2021-03-14 0 867600.0 866385.0 2028.0 3719 1104 0 0 2504 743.8 183164.67857142858 27581.964285714286 null null 743.8 0.0016261119918063891 0.0016261119918063891 0.4004386667119694 -111 220.8 0 0.0 null 1 0 2022-05-09 UGA Uganda 45741007 2021-03-15 0 867600.0 863881.0 2841.0 6223 994 0 0 2504 1037.1666666666667 183164.67857142858 27581.964285714286 null null 1037.1666666666667 0.0022674766794414185 0.0022674766794414185 0.4004386667119694 -110 165.66666666666666 0 0.0 null 1 0 2022-05-09 UGA Uganda 45741007 2021-03-16 0 867600.0 861377.0 4684.0 8727 883 0 0 2504 1246.7142857142858 183164.67857142858 27581.964285714286 null null 1246.7142857142858 0.002725594313466439 0.002725594313466439 0.4004386667119694 -111 126.14285714285714 0 0.0 null 1 0 2022-05-09 UGA Uganda 45741007 2021-03-17 0 867600.0 858873.0 7920.0 11231 773 0 0 2504 1403.875 183164.67857142858 27581.964285714286 0.0 null 1403.875 0.0030691825389852043 0.0030691825389852043 0.4004386667119694 -110 96.625 0 0.0 null 1 0 2022-05-09 UGA Uganda 45741007 2021-03-18 0 867600.0 856369.0 13027.0 13735 662 0 0 2504 1526.111111111111 183164.67857142858 27581.964285714286 202.5 null 1526.111111111111 0.0033364178254997995 0.0033364178254997995 0.4004386667119694 -111 73.55555555555556 0 0.0 null 1 0 2022-05-09 UGA Uganda 45741007 2021-03-19 0 867600.0 853865.0 17543.0 16240 552 0 0 2505 1624.0 183164.67857142858 27581.964285714286 270.0 null 1624.0 0.0035504246769206458 0.0035504246769206458 0.4004386667119694 -110 55.2 0 0.0 null 1 0 2022-05-09 UGA Uganda 45741007 2021-03-20 0 867600.0 851360.0 19008.0 18744 441 0 0 2504 1704.0 183164.67857142858 27581.964285714286 303.75 null 1704.0 0.0037253224442566385 0.0037253224442566385 0.4004386667119694 -111 40.09090909090909 0 0.0 null 1 0 2022-05-09 UGA Uganda 45741007 2021-03-21 0 867600.0 848856.0 23527.0 21248 331 0 0 2504 1770.6666666666667 183164.67857142858 27581.964285714286 743.8 null 1770.6666666666667 0.0038710705837032987 0.0038710705837032987 0.4004386667119694 -110 27.583333333333332 0 0.0 null 1 0 2022-05-09 UGA Uganda 45741007 2021-03-22 0 867600.0 846352.0 25860.0 23752 220 0 0 2504 1827.076923076923 183164.67857142858 27581.964285714286 1037.1666666666667 null 1827.076923076923 0.003994395932465857 0.003994395932465857 0.4004386667119694 -111 16.923076923076923 0 0.0 null 1 0 2022-05-09 UGA Uganda 45741007 2021-03-23 0 867600.0 843848.0 32526.0 26256 110 0 0 2504 1875.4285714285713 183164.67857142858 27581.964285714286 1246.7142

iso_code entity_name population date is_original_reported cumulative_doses_received effective_supply total_doses_owid total_doses at_least_one_dose fully_vaccinated persons_booster_add_dose daily_rate_td rolling_4_week_avg_td max_rolling_4_week_avg_td med_rolling_4_week_avg_td rolling_4_week_avg_td_lastweek rolling_4_week_avg_td_lastmonth rolling_8_week_avg_td rolling_4_week_avg_td_per100 rolling_8_week_avg_td_per100 max_rolling_4_week_avg_td_per100 daily_rate_1d rolling_4_week_avg_1d daily_rate_fv rolling_4_week_avg_fv is_latest is_latest_week_reported no_change_from_previous date_accessed ABW Aruba 106766 2022-04-29 1 170293.0 29.0 170323.0 170293 88370 81923 0 29 34.0 1639.392857142857 264.0 42.964285714285715 48.142857142857146 41.07142857142857 0.03184534402337823 0.03846864036437496 1.5355008683877425 16 16.107142857142858 14 17.892857142857142 1 0 0 2022-05-09 AFG Afghanistan 38928346 2022-05-08 1 1.1671965E7 5649193.0 null 6023425 5320381 4670950 0 653 4004.964285714286 51831.142857142855 11520.107142857143 4873.357142857143 8993.892857142857 6499.428571428572 0.010288041227629567 0.016695876499424278 0.13314499120292153 633 3518.5714285714284 651 3682.285714285714 1 1 0 2022-05-09 ALB Albania 2877800 2022-04-24 1 2837346.0 1425.0 2837346.0 2837346 1311182 1235239 290925 1425 1720.5714285714287 13059.42857142857 6314.678571428572 1793.5 2251.1071428571427 1985.8392857142858 0.05978773467827606 0.06900546548454672 0.4537990329914717 303 355.39285714285717 400 435.07142857142856 1 0 0 2022-05-09 ARE United Arab Emirates 9890402 2022-05-05 1 2.4749854E7 10021.0 2.4699920533333335E7 24749854 9991089 9763292 4995473 10021 6287.535714285715 76720.53571428571 51958.92857142857 6732.357142857143 10170.357142857143 8228.94642857143 0.06357209458509082 0.08320133426903607 0.7757069501753894 0 0.0 0 1534.357142857143 1 0 0 2022-05-09 ARM Armenia 2963234 2022-04-17 1 2479824.0 325779.0 2154689.0 2154689 1131339 987673 41766 644 1702.0357142857142 15883.42857142857 3836.5 2186.4285714285716 3569.3571428571427 2635.6964285714284 0.05743845117482163 0.08894661807239754 0.5360166821597137 147 452.32142857142856 401 1019.8928571428571 1 0 0 2022-05-09 ATG Antigua and Barbuda 97929 2022-04-29 1 224775.0 89170.0 null 135605 63952 61815 9838 0 5.785714285714286 1289.4736842105262 241.85714285714286 364.9642857142857 371.85714285714283 188.82142857142858 0.0059080704241994565 0.19281461933791685 1.316743440870964 0 1.2142857142857142 0 4.571428571428571 1 0 1 2022-05-09 AUS Australia 25499884 2022-05-01 1 5.7759823E7 42173.0 5.7235026E7 57759823 22279275 21528799 13426952 42173 40498.32142857143 282137.5714285714 115068.10714285714 44373.96428571428 71230.10714285714 55864.21428571428 0.15881766924340293 0.2190763467226529 1.1064268818970762 1571 2143.035714285714 5330 8507.32142857143 1 0 0 2022-05-09 AZE Azerbaijan 10139175 2022-04-24 1 1.35132444E7 18174.400000000373 1.3627588E7 13499692 5362072 4843392 3294230 4622 7911.607142857143 64913.21428571428 29178.10714285714 9341.57142857143 15137.107142857143 11524.357142857143 0.07803008768323993 0.11366168492857795 0.6402218551875698 445 579.8214285714286 281 702.1071428571429 1 0 0 2022-05-09 BFA Burkina Faso 20903273 2022-05-01 1 5526585.0 2597596.0 2928989.0 2928989 2434140 1539151 0 0 18102.5 27639.285714285714 3936.785714285714 19042.35714285714 3288.1071428571427 10695.30357142857 0.08660127052830434 0.05116568860497862 0.13222467942836374 594 10089.107142857143 530 11081.57142857143 1 1 1 2022-05-09 BGD Bangladesh 164689383 2022-04-30 1 4.885076682E8 2.308764402E8 null 257793811 128568620 116425878 12799313 162583 316767.53571428574 1811898.142857143 444306.14285714284 715956.9642857143 1179345.392857143 748056.4642857143 0.19234241451635395 0.4542226406214141 1.1001912265693188 10412 25093.428571428572 52480 173990.0357142857 1 0 0 2022-05-09 BHR Bahrain 1701575 2022-05-08 1 3436743.0 296.0 null 3436743 1234889 1219122 982732 296 314.5357142857143 11411.857142857143 8157.1666666666

iso_code entity_name population date is_original_reported cumulative_doses_received effective_supply total_doses_owid total_doses at_least_one_dose fully_vaccinated persons_booster_add_dose daily_rate_td rolling_4_week_avg_td max_rolling_4_week_avg_td med_rolling_4_week_avg_td rolling_4_week_avg_td_lastweek rolling_4_week_avg_td_lastmonth rolling_8_week_avg_td rolling_4_week_avg_td_per100 rolling_8_week_avg_td_per100 max_rolling_4_week_avg_td_per100 daily_rate_1d rolling_4_week_avg_1d daily_rate_fv rolling_4_week_avg_fv is_latest is_latest_week_reported no_change_from_previous date_accessed AFG Afghanistan 38928346 2021-02-22 0 450000.0 null 0.0 0 0 0 0 0 0.0 51831.142857142855 11520.107142857143 null null 0.0 0.0 0.0 0.13314499120292153 0 0.0 0 0.0 null 1 0 2022-05-09 AFG Afghanistan 38928346 2021-02-23 0 450000.0 450000.0 1366.6666666666667 2396 0 0 0 2396 1198.0 51831.142857142855 11520.107142857143 null null 1198.0 0.003077449013631352 0.003077449013631352 0.13314499120292153 0 0.0 0 0.0 null 1 0 2022-05-09 AFG Afghanistan 38928346 2021-02-24 0 450000.0 447604.0 2733.3333333333335 4792 0 0 0 2396 1597.3333333333333 51831.142857142855 11520.107142857143 null null 1597.3333333333333 0.00410326535150847 0.00410326535150847 0.13314499120292153 0 0.0 0 0.0 null 1 0 2022-05-09 AFG Afghanistan 38928346 2021-02-25 0 450000.0 445208.0 4100.0 7188 0 0 0 2396 1797.0 51831.142857142855 11520.107142857143 null null 1797.0 0.004616173520447028 0.004616173520447028 0.13314499120292153 0 0.0 0 0.0 null 1 0 2022-05-09 AFG Afghanistan 38928346 2021-02-26 0 450000.0 442812.0 5466.666666666667 9584 0 0 0 2396 1916.8 51831.142857142855 11520.107142857143 null null 1916.8 0.004923918421810163 0.004923918421810163 0.13314499120292153 0 0.0 0 0.0 null 1 0 2022-05-09 AFG Afghanistan 38928346 2021-02-27 0 450000.0 440416.0 6833.333333333334 11980 0 0 0 2396 1996.6666666666667 51831.142857142855 11520.107142857143 null null 1996.6666666666667 0.005129081689385587 0.005129081689385587 0.13314499120292153 0 0.0 0 0.0 null 1 0 2022-05-09 AFG Afghanistan 38928346 2021-02-28 0 450000.0 438020.0 8200.0 14376 0 0 0 2396 2053.714285714286 51831.142857142855 11520.107142857143 null null 2053.714285714286 0.005275626880510889 0.005275626880510889 0.13314499120292153 0 0.0 0 0.0 null 1 0 2022-05-09 AFG Afghanistan 38928346 2021-03-01 0 871200.0 856824.0 11062.5 16773 0 0 0 2397 2096.625 51831.142857142855 11520.107142857143 0.0 null 2096.625 0.005385856876631749 0.005385856876631749 0.13314499120292153 0 0.0 0 0.0 null 1 0 2022-05-09 AFG Afghanistan 38928346 2021-03-02 0 871200.0 854427.0 13925.0 19169 0 0 0 2396 2129.8888888888887 51831.142857142855 11520.107142857143 1198.0 null 2129.8888888888887 0.005471305893368521 0.005471305893368521 0.13314499120292153 0 0.0 0 0.0 null 1 0 2022-05-09 AFG Afghanistan 38928346 2021-03-03 0 871200.0 852031.0 16787.5 21565 0 0 0 2396 2156.5 51831.142857142855 11520.107142857143 1597.3333333333333 null 2156.5 0.005539665106757939 0.005539665106757939 0.13314499120292153 0 0.0 0 0.0 null 1 0 2022-05-09 AFG Afghanistan 38928346 2021-03-04 0 871200.0 849635.0 19650.0 23961 0 0 0 2396 2178.2727272727275 51831.142857142855 11520.107142857143 1797.0 null 2178.2727272727275 0.0055955953722583735 0.0055955953722583735 0.13314499120292153 0 0.0 0 0.0 null 1 0 2022-05-09 AFG Afghanistan 38928346 2021-03-05 0 871200.0 847239.0 22512.5 26357 0 0 0 2396 2196.4166666666665 51831.142857142855 11520.107142857143 1916.8 null 2196.4166666666665 0.005642203926842067 0.005642203926842067 0.13314499120292153 0 0.0 0 0.0 null 1 0 2022-05-09 AFG Afghanistan 38928346 2021-03-06 0 871200.0 844843.0 25375.0 28753 0 0 0 2396 2211.769230769231 51831.142857142855 11520.107142857143 1996.6666666666667 null 2211.769230769231 0.0056816419345667325 0.0056816419345667325 0.13314499120292153 0 0.0 0 0.0 null 1 0 2022-05-09 AFG Afghanistan 38928346 2021-03-07 1 871200.0 842447.0 28237.5 31150 0 0 0 2397 2225.0 51831.142857142855 11520.107142857143 2053.714285

### Save to Azure Storage / Register in Databricks metastore

In [0]:
delta_path = transformed_storage_path + '.delta'

# dbutils.fs.rm(delta_path, True)

df12.write.format("delta").mode("overwrite").save(delta_path)

In [0]:
# path for delta
print(transformed_storage_path + '.delta')

/mnt/covax-supply-chain-analytics/transformed/who/analysis_vx_throughput_output_daily.delta

In [0]:
%sql

DROP TABLE IF EXISTS covax_supply_chain_analytics.analysis_vx_throughput_output_daily;

CREATE TABLE covax_supply_chain_analytics.analysis_vx_throughput_output_daily
USING DELTA
LOCATION '/mnt/covax-supply-chain-analytics/transformed/who/analysis_vx_throughput_output_daily.delta'

In [0]:
display(spark.sql("SELECT * FROM covax_supply_chain_analytics.analysis_vx_throughput_output_daily"))

iso_code entity_name population date is_original_reported cumulative_doses_received effective_supply total_doses_owid total_doses at_least_one_dose fully_vaccinated persons_booster_add_dose daily_rate_td rolling_4_week_avg_td max_rolling_4_week_avg_td med_rolling_4_week_avg_td rolling_4_week_avg_td_lastweek rolling_4_week_avg_td_lastmonth rolling_8_week_avg_td rolling_4_week_avg_td_per100 rolling_8_week_avg_td_per100 max_rolling_4_week_avg_td_per100 daily_rate_1d rolling_4_week_avg_1d daily_rate_fv rolling_4_week_avg_fv is_latest is_latest_week_reported no_change_from_previous date_accessed ABW Aruba 106766 2021-02-17 0 null null null 0 0 0 0 0 0.0 1639.392857142857 264.0 null null 0.0 0.0 0.0 1.5355008683877425 0 0.0 0 0.0 null 0 0 2022-05-09 ABW Aruba 106766 2021-02-18 0 null null null 6 6 0 0 6 3.0 1639.392857142857 264.0 null null 3.0 0.0028098832961804317 0.0028098832961804317 1.5355008683877425 6 3.0 0 0.0 null 0 0 2022-05-09 ABW Aruba 106766 2021-02-19 1 null null null 12 12 0 0 6 4.0 1639.392857142857 264.0 null null 4.0 0.003746511061573909 0.003746511061573909 1.5355008683877425 6 4.0 0 0.0 0 0 0 2022-05-09 ABW Aruba 106766 2021-02-20 0 null null null 424 424 0 0 412 106.0 1639.392857142857 264.0 null null 106.0 0.09928254313170859 0.09928254313170859 1.5355008683877425 412 106.0 0 0.0 null 0 0 2022-05-09 ABW Aruba 106766 2021-02-21 0 null null null 836 836 0 0 412 167.2 1639.392857142857 264.0 null null 167.2 0.1566041623737894 0.1566041623737894 1.5355008683877425 412 167.2 0 0.0 null 0 0 2022-05-09 ABW Aruba 106766 2021-02-22 0 null null null 1248 1248 0 0 412 208.0 1639.392857142857 264.0 null null 208.0 0.19481857520184329 0.19481857520184329 1.5355008683877425 412 208.0 0 0.0 null 0 0 2022-05-09 ABW Aruba 106766 2021-02-23 0 null null null 1660 1660 0 0 412 237.14285714285714 1639.392857142857 264.0 null null 237.14285714285714 0.22211458436473894 0.22211458436473894 1.5355008683877425 412 237.14285714285714 0 0.0 null 0 0 2022-05-09 ABW Aruba 106766 2021-02-24 0 null null null 2072 2072 0 0 412 259.0 1639.392857142857 264.0 0.0 null 259.0 0.24258659123691062 0.24258659123691062 1.5355008683877425 412 259.0 0 0.0 null 0 0 2022-05-09 ABW Aruba 106766 2021-02-25 0 null null null 2484 2484 0 0 412 276.0 1639.392857142857 264.0 3.0 null 276.0 0.25850926324859974 0.25850926324859974 1.5355008683877425 412 276.0 0 0.0 null 0 0 2022-05-09 ABW Aruba 106766 2021-02-26 1 null null null 2896 2896 0 0 412 289.6 1639.392857142857 264.0 4.0 null 289.6 0.27124740085795107 0.27124740085795107 1.5355008683877425 412 289.6 0 0.0 0 0 0 2022-05-09 ABW Aruba 106766 2021-02-27 0 null null null 3751 3751 0 0 855 341.0 1639.392857142857 264.0 106.0 null 341.0 0.3193900679991758 0.3193900679991758 1.5355008683877425 855 341.0 0 0.0 null 0 0 2022-05-09 ABW Aruba 106766 2021-02-28 0 null null null 4606 4606 0 0 855 383.8333333333333 1639.392857142857 264.0 167.2 null 383.8333333333333 0.3595089572835297 0.3595089572835297 1.5355008683877425 855 383.8333333333333 0 0.0 null 0 0 2022-05-09 ABW Aruba 106766 2021-03-01 0 25508.7 20902.7 null 5461 5461 0 0 855 420.0769230769231 1639.392857142857 264.0 208.0 null 420.0769230769231 0.3934557097549062 0.3934557097549062 1.5355008683877425 855 420.0769230769231 0 0.0 null 0 0 2022-05-09 ABW Aruba 106766 2021-03-02 0 25508.7 20047.7 null 6316 6316 0 0 855 451.14285714285717 1639.392857142857 264.0 237.14285714285714 null 451.14285714285717 0.42255292615894313 0.42255292615894313 1.5355008683877425 855 451.14285714285717 0 0.0 null 0 0 2022-05-09 ABW Aruba 106766 2021-03-03 0 25508.7 19192.7 null 7171 7171 0 0 855 478.06666666666666 1639.392857142857 264.0 259.0 null 478.06666666666666 0.44777051370910836 0.44777051370910836 1.5355008683877425 855 478.06666666666666 0 0.0 null 0 0 2022-05-09 ABW Aruba 106766 2021-03-04 0 25508.7 18337.7 null 8026 8026 0 0 855 501.625 1639.392857142857 264.0 276.0 null 501.625 0.469835902815503 0.469835902815503 1.5355008683877425 855 501.625 0 0.0 null 0 0 2022-05-

In [0]:
display(spark.sql("SELECT * FROM covax_supply_chain_analytics.analysis_vx_throughput_output_daily").orderBy(['iso_code', 'date']).filter(col('iso_code')==iso_code))

iso_code entity_name population date is_original_reported cumulative_doses_received effective_supply total_doses_owid total_doses at_least_one_dose fully_vaccinated persons_booster_add_dose daily_rate_td rolling_4_week_avg_td max_rolling_4_week_avg_td med_rolling_4_week_avg_td rolling_4_week_avg_td_lastweek rolling_4_week_avg_td_lastmonth rolling_8_week_avg_td rolling_4_week_avg_td_per100 rolling_8_week_avg_td_per100 max_rolling_4_week_avg_td_per100 daily_rate_1d rolling_4_week_avg_1d daily_rate_fv rolling_4_week_avg_fv is_latest is_latest_week_reported no_change_from_previous date_accessed UGA Uganda 45741007 2021-03-10 0 867600.0 null 338.3333333333333 0 0 0 0 0 0.0 183164.67857142858 27581.964285714286 null null 0.0 0.0 0.0 0.4004386667119694 0 0.0 0 0.0 null 1 0 2022-05-09 UGA Uganda 45741007 2021-03-11 0 867600.0 867600.0 676.6666666666666 405 405 0 0 405 202.5 183164.67857142858 27581.964285714286 null null 202.5 4.427099735692308E-4 4.427099735692308E-4 0.4004386667119694 405 202.5 0 0.0 null 1 0 2022-05-09 UGA Uganda 45741007 2021-03-12 0 867600.0 867195.0 1015.0 810 810 0 0 405 270.0 183164.67857142858 27581.964285714286 null null 270.0 5.902799647589744E-4 5.902799647589744E-4 0.4004386667119694 405 270.0 0 0.0 null 1 0 2022-05-09 UGA Uganda 45741007 2021-03-13 1 867600.0 866790.0 1215.0 1215 1215 0 0 405 303.75 183164.67857142858 27581.964285714286 null null 303.75 6.640649603538462E-4 6.640649603538462E-4 0.4004386667119694 405 303.75 0 0.0 0 1 0 2022-05-09 UGA Uganda 45741007 2021-03-14 0 867600.0 866385.0 2028.0 3719 1104 0 0 2504 743.8 183164.67857142858 27581.964285714286 null null 743.8 0.0016261119918063891 0.0016261119918063891 0.4004386667119694 -111 220.8 0 0.0 null 1 0 2022-05-09 UGA Uganda 45741007 2021-03-15 0 867600.0 863881.0 2841.0 6223 994 0 0 2504 1037.1666666666667 183164.67857142858 27581.964285714286 null null 1037.1666666666667 0.0022674766794414185 0.0022674766794414185 0.4004386667119694 -110 165.66666666666666 0 0.0 null 1 0 2022-05-09 UGA Uganda 45741007 2021-03-16 0 867600.0 861377.0 4684.0 8727 883 0 0 2504 1246.7142857142858 183164.67857142858 27581.964285714286 null null 1246.7142857142858 0.002725594313466439 0.002725594313466439 0.4004386667119694 -111 126.14285714285714 0 0.0 null 1 0 2022-05-09 UGA Uganda 45741007 2021-03-17 0 867600.0 858873.0 7920.0 11231 773 0 0 2504 1403.875 183164.67857142858 27581.964285714286 0.0 null 1403.875 0.0030691825389852043 0.0030691825389852043 0.4004386667119694 -110 96.625 0 0.0 null 1 0 2022-05-09 UGA Uganda 45741007 2021-03-18 0 867600.0 856369.0 13027.0 13735 662 0 0 2504 1526.111111111111 183164.67857142858 27581.964285714286 202.5 null 1526.111111111111 0.0033364178254997995 0.0033364178254997995 0.4004386667119694 -111 73.55555555555556 0 0.0 null 1 0 2022-05-09 UGA Uganda 45741007 2021-03-19 0 867600.0 853865.0 17543.0 16240 552 0 0 2505 1624.0 183164.67857142858 27581.964285714286 270.0 null 1624.0 0.0035504246769206458 0.0035504246769206458 0.4004386667119694 -110 55.2 0 0.0 null 1 0 2022-05-09 UGA Uganda 45741007 2021-03-20 0 867600.0 851360.0 19008.0 18744 441 0 0 2504 1704.0 183164.67857142858 27581.964285714286 303.75 null 1704.0 0.0037253224442566385 0.0037253224442566385 0.4004386667119694 -111 40.09090909090909 0 0.0 null 1 0 2022-05-09 UGA Uganda 45741007 2021-03-21 0 867600.0 848856.0 23527.0 21248 331 0 0 2504 1770.6666666666667 183164.67857142858 27581.964285714286 743.8 null 1770.6666666666667 0.0038710705837032987 0.0038710705837032987 0.4004386667119694 -110 27.583333333333332 0 0.0 null 1 0 2022-05-09 UGA Uganda 45741007 2021-03-22 0 867600.0 846352.0 25860.0 23752 220 0 0 2504 1827.076923076923 183164.67857142858 27581.964285714286 1037.1666666666667 null 1827.076923076923 0.003994395932465857 0.003994395932465857 0.4004386667119694 -111 16.923076923076923 0 0.0 null 1 0 2022-05-09 UGA Uganda 45741007 2021-03-23 0 867600.0 843848.0 32526.0 26256 110 0 0 2504 1875.4285714285713 183164.67857142858 27581.964285714286 1246.7142

In [0]:
display(
  spark.sql("SELECT * FROM covax_supply_chain_analytics.analysis_vx_throughput_output_daily")
    .select('iso_code', 'date', 'max_rolling_4_week_avg_td', 'rolling_4_week_avg_td') \
    .orderBy(['iso_code', 'date'])
    .filter(col('iso_code')==iso_code)
)

iso_code date max_rolling_4_week_avg_td rolling_4_week_avg_td UGA 2021-03-10 183164.67857142858 0.0 UGA 2021-03-11 183164.67857142858 202.5 UGA 2021-03-12 183164.67857142858 270.0 UGA 2021-03-13 183164.67857142858 303.75 UGA 2021-03-14 183164.67857142858 743.8 UGA 2021-03-15 183164.67857142858 1037.1666666666667 UGA 2021-03-16 183164.67857142858 1246.7142857142858 UGA 2021-03-17 183164.67857142858 1403.875 UGA 2021-03-18 183164.67857142858 1526.111111111111 UGA 2021-03-19 183164.67857142858 1624.0 UGA 2021-03-20 183164.67857142858 1704.0 UGA 2021-03-21 183164.67857142858 1770.6666666666667 UGA 2021-03-22 183164.67857142858 1827.076923076923 UGA 2021-03-23 183164.67857142858 1875.4285714285713 UGA 2021-03-24 183164.67857142858 1917.4 UGA 2021-03-25 183164.67857142858 2463.125 UGA 2021-03-26 183164.67857142858 2944.6470588235293 UGA 2021-03-27 183164.67857142858 3075.3333333333335 UGA 2021-03-28 183164.67857142858 3192.315789473684 UGA 2021-03-29 183164.67857142858 3297.6 UGA 2021-03-30 183164.67857142858 3392.809523809524 UGA 2021-03-31 183164.67857142858 3479.409090909091 UGA 2021-04-01 183164.67857142858 3558.478260869565 UGA 2021-04-02 183164.67857142858 3630.9166666666665 UGA 2021-04-03 183164.67857142858 3697.6 UGA 2021-04-04 183164.67857142858 3759.153846153846 UGA 2021-04-05 183164.67857142858 3816.1481481481483 UGA 2021-04-06 183164.67857142858 4077.464285714286 UGA 2021-04-07 183164.67857142858 4475.071428571428 UGA 2021-04-08 183164.67857142858 4858.214285714285 UGA 2021-04-09 183164.67857142858 5241.392857142857 UGA 2021-04-10 183164.67857142858 5624.535714285715 UGA 2021-04-11 183164.67857142858 5932.714285714285 UGA 2021-04-12 183164.67857142858 6240.928571428572 UGA 2021-04-13 183164.67857142858 6635.5 UGA 2021-04-14 183164.67857142858 7030.107142857143 UGA 2021-04-15 183164.67857142858 6945.178571428572 UGA 2021-04-16 183164.67857142858 6860.25 UGA 2021-04-17 183164.67857142858 6775.357142857143 UGA 2021-04-18 183164.67857142858 6690.464285714285 UGA 2021-04-19 183164.67857142858 6605.571428571428 UGA 2021-04-20 183164.67857142858 6943.321428571428 UGA 2021-04-21 183164.67857142858 7281.071428571428 UGA 2021-04-22 183164.67857142858 6900.75 UGA 2021-04-23 183164.67857142858 6520.428571428572 UGA 2021-04-24 183164.67857142858 6331.25 UGA 2021-04-25 183164.67857142858 6142.035714285715 UGA 2021-04-26 183164.67857142858 5952.821428571428 UGA 2021-04-27 183164.67857142858 5763.642857142857 UGA 2021-04-28 183164.67857142858 5574.428571428572 UGA 2021-04-29 183164.67857142858 6257.392857142857 UGA 2021-04-30 183164.67857142858 6940.392857142857 UGA 2021-05-01 183164.67857142858 7623.357142857143 UGA 2021-05-02 183164.67857142858 8306.32142857143 UGA 2021-05-03 183164.67857142858 8989.285714285714 UGA 2021-05-04 183164.67857142858 8591.67857142857 UGA 2021-05-05 183164.67857142858 8194.07142857143 UGA 2021-05-06 183164.67857142858 8091.928571428572 UGA 2021-05-07 183164.67857142858 7989.75 UGA 2021-05-08 183164.67857142858 7887.642857142857 UGA 2021-05-09 183164.67857142858 7785.5 UGA 2021-05-10 183164.67857142858 7683.357142857143 UGA 2021-05-11 183164.67857142858 7199.357142857143 UGA 2021-05-12 183164.67857142858 6715.321428571428 UGA 2021-05-13 183164.67857142858 6710.821428571428 UGA 2021-05-14 183164.67857142858 6706.285714285715 UGA 2021-05-15 183164.67857142858 7112.571428571428 UGA 2021-05-16 183164.67857142858 7518.892857142857 UGA 2021-05-17 183164.67857142858 7925.178571428572 UGA 2021-05-18 183164.67857142858 7908.857142857143 UGA 2021-05-19 183164.67857142858 7892.464285714285 UGA 2021-05-20 183164.67857142858 8303.32142857143 UGA 2021-05-21 183164.67857142858 8714.17857142857 UGA 2021-05-22 183164.67857142858 8980.142857142857 UGA 2021-05-23 183164.67857142858 9246.142857142857 UGA 2021-05-24 183164.67857142858 9512.142857142857 UGA 2021-05-25 183164.67857142858 10236.57142857143 UGA 2021-05-26 183164.67857142858 10961.035714285714 UGA 2021-05-27 183164.67857142858 10554.607142857143 UGA 2021-05-28 183164

##### Query Delta Log

In [0]:
display(
  spark.sql("DESCRIBE HISTORY delta. `/mnt/covax-supply-chain-analytics/transformed/who/analysis_vx_throughput_output_daily.delta`")
)

version timestamp userId userName operation operationParameters job notebook clusterId readVersion isolationLevel isBlindAppend operationMetrics userMetadata 25 2022-05-09T20:50:48.000+0000 6136552160696939 jeremy.cooper@gatesfoundation.org WRITE Map(mode -> Overwrite, partitionBy -> []) null List(4454943111335582) 1112-212424-shuwbub0 24 WriteSerializable false Map(numFiles -> 2, numOutputRows -> 92208, numOutputBytes -> 7023761) null 24 2022-05-03T17:33:32.000+0000 6136552160696939 jeremy.cooper@gatesfoundation.org WRITE Map(mode -> Overwrite, partitionBy -> []) null List(4454943111335582) 1112-212424-shuwbub0 23 WriteSerializable false Map(numFiles -> 9, numOutputRows -> 91157, numOutputBytes -> 6966712) null 23 2022-04-26T03:22:15.000+0000 6136552160696939 jeremy.cooper@gatesfoundation.org WRITE Map(mode -> Overwrite, partitionBy -> []) null List(4454943111335582) 1112-212424-shuwbub0 22 WriteSerializable false Map(numFiles -> 2, numOutputRows -> 88256, numOutputBytes -> 6733361) null 22 2022-04-18T22:53:23.000+0000 6136552160696939 jeremy.cooper@gatesfoundation.org WRITE Map(mode -> Overwrite, partitionBy -> []) null List(4454943111335582) 1112-212424-shuwbub0 21 WriteSerializable false Map(numFiles -> 2, numOutputRows -> 87343, numOutputBytes -> 6659995) null 21 2022-04-11T22:19:55.000+0000 6136552160696939 jeremy.cooper@gatesfoundation.org WRITE Map(mode -> Overwrite, partitionBy -> []) null List(4454943111335582) 1112-212424-shuwbub0 20 WriteSerializable false Map(numFiles -> 2, numOutputRows -> 85893, numOutputBytes -> 6547053) null 20 2022-04-11T22:17:51.000+0000 6136552160696939 jeremy.cooper@gatesfoundation.org WRITE Map(mode -> Overwrite, partitionBy -> []) null List(4454943111335582) 1112-212424-shuwbub0 19 WriteSerializable false Map(numFiles -> 2, numOutputRows -> 85893, numOutputBytes -> 6547053) null 19 2022-04-04T20:00:58.000+0000 6136552160696939 jeremy.cooper@gatesfoundation.org WRITE Map(mode -> Overwrite, partitionBy -> []) null List(4454943111335582) 1112-212424-shuwbub0 18 WriteSerializable false Map(numFiles -> 2, numOutputBytes -> 6340416, numOutputRows -> 83633) null 18 2022-03-28T22:45:02.000+0000 6136552160696939 jeremy.cooper@gatesfoundation.org WRITE Map(mode -> Overwrite, partitionBy -> []) null List(4454943111335582) 1112-212424-shuwbub0 17 WriteSerializable false Map(numFiles -> 2, numOutputBytes -> 6326584, numOutputRows -> 83498) null 17 2022-03-21T18:22:05.000+0000 6136552160696939 jeremy.cooper@gatesfoundation.org WRITE Map(mode -> Overwrite, partitionBy -> []) null List(4454943111335582) 1112-212424-shuwbub0 16 WriteSerializable false Map(numFiles -> 7, numOutputBytes -> 6152874, numOutputRows -> 81264) null 16 2022-03-15T01:32:56.000+0000 6136552160696939 jeremy.cooper@gatesfoundation.org WRITE Map(mode -> Overwrite, partitionBy -> []) null List(4454943111335582) 1112-212424-shuwbub0 15 WriteSerializable false Map(numFiles -> 1, numOutputBytes -> 6001362, numOutputRows -> 78850) null 15 2022-03-07T14:33:50.000+0000 6136552160696939 jeremy.cooper@gatesfoundation.org WRITE Map(mode -> Overwrite, partitionBy -> []) null List(4454943111335582) 1112-212424-shuwbub0 14 WriteSerializable false Map(numFiles -> 1, numOutputBytes -> 5975465, numOutputRows -> 78553) null 14 2022-03-07T14:30:48.000+0000 6136552160696939 jeremy.cooper@gatesfoundation.org WRITE Map(mode -> Overwrite, partitionBy -> []) null List(4454943111335582) 1112-212424-shuwbub0 13 WriteSerializable false Map(numFiles -> 7, numOutputBytes -> 5938212, numOutputRows -> 78553) null 13 2022-03-07T14:03:34.000+0000 6136552160696939 jeremy.cooper@gatesfoundation.org WRITE Map(mode -> Overwrite, partitionBy -> []) null List(4454943111335582) 1112-212424-shuwbub0 12 WriteSerializable false Map(numFiles -> 1, numOutputBytes -> 5933640, numOutputRows -> 77799) null 12 2022-03-01T22:08:44.000+0000 6136552160696939 jeremy.cooper@gatesfoundation.org WRITE Map(mode -> Overwrite, partitionBy -> []) null List(4454943111335582) 1112-212424-shuwb

### Appendix

In [0]:
display(
  spark.sql("SELECT * FROM covax_supply_chain_analytics.analysis_vx_throughput_output_daily")
    .filter(col('is_latest')==1)
)

iso_code entity_name population date is_original_reported cumulative_doses_received effective_supply total_doses_owid total_doses at_least_one_dose fully_vaccinated persons_booster_add_dose daily_rate_td rolling_4_week_avg_td max_rolling_4_week_avg_td med_rolling_4_week_avg_td rolling_4_week_avg_td_lastweek rolling_4_week_avg_td_lastmonth rolling_8_week_avg_td rolling_4_week_avg_td_per100 rolling_8_week_avg_td_per100 max_rolling_4_week_avg_td_per100 daily_rate_1d rolling_4_week_avg_1d daily_rate_fv rolling_4_week_avg_fv is_latest is_latest_week_reported no_change_from_previous date_accessed AGO Angola 32866272 2022-05-08 1 2.4790212E7 6893586.0 null 17896626 12059919 6327907 369899 0 7321.928571428572 113251.14285714286 22237.10714285714 9762.57142857143 21879.0 14600.464285714286 0.02227794065426274 0.04442385277440133 0.34458165153973913 0 16720.14285714286 0 6772.607142857143 1 1 1 2022-05-09 AIA Anguilla 15002 2022-04-29 1 23126.0 0.0 23315.0 23126 10622 9874 2630 0 14.714285714285714 236.96428571428572 32.357142857142854 14.714285714285714 12.035714285714286 13.375 0.09808216047384158 0.08915477936275164 1.579551297922182 0 1.7857142857142858 0 8.928571428571429 1 0 1 2022-05-09 AND Andorra 77265 2022-04-24 1 152463.0 12.0 152463.0 152463 57866 53414 41183 12 9.857142857142858 1157.5 290.5357142857143 10.357142857142858 23.785714285714285 16.821428571428573 0.012757578278836288 0.02177108467149236 1.4980909855691453 2 1.1071428571428572 1 0.8928571428571429 1 0 0 2022-05-09 ARG Argentina 45195774 2022-04-29 1 1.057963644E8 7391185.400000006 9.8819521E7 98484287 41017420 37222311 20555542 79108 63413.642857142855 358555.1785714286 248174.07142857142 61931.25 104055.92857142857 83734.78571428571 0.1403087882887963 0.1852712727395391 0.79333784298379 2769 3459.25 8118 9129.07142857143 1 0 0 2022-05-09 ASM American Samoa 55197 2022-04-21 1 null null null 105958 44240 40593 21694 207 239.5 445.9642857142857 200.57142857142858 255.89285714285714 438.89285714285717 339.19642857142856 0.4339003931373082 0.614519681452667 0.8079502250381102 5 15.142857142857142 39 41.107142857142854 1 0 0 2022-05-09 AUT Austria 8901064 2022-04-24 1 3.4687728E7 1.643584E7 1.8261423285714287E7 18254793 6821795 6605084 5178777 2905 8665.642857142857 133023.32142857142 25311.85714285714 8783.785714285714 4058.1428571428573 6361.892857142857 0.09735513481470144 0.07147339753025994 1.4944653968174075 236 273.60714285714283 434 490.35714285714283 1 0 0 2022-05-09 BDI Burundi 11890784 2022-05-08 1 586080.0 573456.0 null 12651 12651 12078 0 27 6.678571428571429 163.46428571428572 56.392857142857146 0.0 19.75 13.214285714285714 5.6165946909568187E-5 1.1113048319005469E-4 0.0013747141123267037 71 41.214285714285715 71 39.785714285714285 1 1 0 2022-05-09 BEL Belgium 11522440 2022-04-24 1 2.5292607E7 2069.0 2.5308942E7 25292607 9227575 9129979 7125339 2069 17040.214285714286 140314.25 47350.5 17149.25 4015.6071428571427 10527.910714285714 0.14788720345442707 0.09136876142801102 1.217747716629464 235 187.85714285714286 332 371.60714285714283 1 0 0 2022-05-09 BEN Benin 12123200 2022-05-08 1 4823766.0 1672884.0 null 3152148 3157864 2625325 0 1266 1265.4642857142858 41237.607142857145 2187.214285714286 1334.5714285714287 1697.607142857143 1481.5357142857142 0.010438368464714645 0.012220665453722732 0.3401544735949019 2990 2989.5714285714284 3380 3379.464285714286 1 1 0 2022-05-09 BGR Bulgaria 6951482 2022-04-24 1 1.172781E7 7351171.0 4376629.5 4377438 2086746 2056552 739107 799 1132.3214285714287 19972.39285714286 8736.67857142857 1282.9642857142858 1692.1785714285713 1412.25 0.01628892124832415 0.020315811793801666 0.2873112935794534 109 152.32142857142858 132 189.64285714285714 1 0 0 2022-05-09 BIH Bosnia and Herzegovina 3280815 2022-01-29 1 2403972.0 571791.0 1924950.0 1924950 943394 846080 0 92769 13252.714285714286 13252.714285714286 6771.607142857143 0.0 0.0 6626.357142857143 0.4039457965692758 0.2019728982846379 0.4039457965692758 15189 2169.75 31363 15510.